# Preperation

In [1]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
!pip install transformers
!pip install sentencepiece
!pip install transformers[sentencepiece]
!pip install bitsandbytes
!pip install datasets
!pip install peft
!pip install trl
!pip install suffix_tree
!pip install ftfy

In [ ]:
gpu_info = !nvidia-smi
gpu_info = '\n'.join(gpu_info)
if gpu_info.find('failed') >= 0:
  print('Not connected to a GPU')
else:
  print(gpu_info)

In [ ]:
import sys
sys.path.insert(0,'/content/drive/MyDrive/thesis')
from importlib import reload

In [ ]:
from datasets import load_dataset, Dataset

In [ ]:
import pandas as pd
pd.set_option("display.max_colwidth", None)

In [ ]:
import acmodel as acm
import eval_acm as eac
from utils import *

#Recipes

In [8]:
import os
WORKDIR = "/content/drive/MyDrive/thesis/recipes_run_24_7_5"
if not os.path.exists(WORKDIR):
  os.makedirs(WORKDIR)
DATA_DIR = "/content/drive/MyDrive/thesis/recipes"

##Data loading and processing

###Loading

In [9]:
recipes_df = pd.read_csv(DATA_DIR + "/archive/RAW_recipes.csv")[['id', 'name', 'tags', 'steps', 'description']]
recipes_df['steps'] = recipes_df['steps'].apply(lambda x: ". ".join(eval(x)))
recipes_df['tags'] = recipes_df['tags'].apply(lambda x: eval(x))
recipes_df['description'] = recipes_df['description'].apply(lambda x: x.replace("\r\n"," ").replace("  "," ") if type(x) == str else x)

In [10]:
import pickle
ingr_df = pd.read_csv(DATA_DIR + "/archive/PP_recipes.csv")[['id', 'ingredient_ids']]
ingr_map = pickle.load(open(DATA_DIR + "/archive/ingr_map_parsed.pkl","rb"))
ingr_df['ingredients'] = [[ingr_map[i] for i in eval(ingr_df['ingredient_ids'][j])] for j in range(len(ingr_df))]
recipes_df = pd.merge(recipes_df, ingr_df, on='id')

In [11]:
dishes = open(DATA_DIR + "/classes.txt","r").read().splitlines()
dishes = [c.replace("_"," ") for c in dishes]

###Choosing dishes

In [12]:
dish_count = {d:0 for d in dishes}
dish_per_recipe = []
for name in recipes_df['name']:
  for d in dishes:
    if d in name:
      dish_per_recipe.append(d)
      dish_count[d] += 1
      break
  else:
    dish_per_recipe.append("")
recipes_df['dish'] = dish_per_recipe

In [13]:
most_common = sorted(dish_count.items(), key=lambda x: x[1], reverse=True)
chosen_dishes = most_common[:10]
dishes_set = set([dish for dish,_ in chosen_dishes])

In [14]:
chosen_dishes

[('steak', 2283),
 ('pizza', 1879),
 ('pork chop', 1457),
 ('pancakes', 1200),
 ('cheesecake', 1151),
 ('ice cream', 698),
 ('lasagna', 620),
 ('hamburger', 570),
 ('french toast', 563),
 ('macaroni and cheese', 408)]

###Identifying secret ingredients

In [15]:
all_ingr = [recipes_df[recipes_df['dish']==dish]['ingredients'] for dish,_ in chosen_dishes]

In [16]:
from collections import Counter
all_ing = [[] for i in range(len(chosen_dishes))]
for i,r in enumerate(all_ingr):
  for l in r:
    all_ing[i].extend(l)
counts = [Counter(all_ing[i]) for i in range(len(all_ing))]
total_count = Counter()
for c in counts:
  total_count += c

In [17]:
import numpy as np
p_thresh = 0.05
mul_thresh = 10
total_amount = sum([v for k,v in chosen_dishes])

dish2secret_ing = {d:[] for d,_ in chosen_dishes}
for i,c in enumerate(counts):
  name, amount = chosen_dishes[i]
  m_c = total_count - c
  m_amount = total_amount - amount
  for k,v in c.items():
    p = v / amount
    tp = m_c[k] / m_amount
    lp = []
    for i2,c2 in enumerate(counts):
      name2, amount2 = chosen_dishes[i2]
      v2 = c2[k]
      p2 = v2 / amount2
      lp.append(round(np.log2(p2),1))
    if p > p_thresh and p > tp * mul_thresh:
      dish2secret_ing[name].append((k, np.log2(p), p / (tp+0.000000001), lp))

<ipython-input-17-f43da58379e2>:19: RuntimeWarning: divide by zero encountered in log2
  lp.append(round(np.log2(p2),1))


In [18]:
dish2secret = {k:[x[0] for x in dish2secret_ing[k]] for k in dish2secret_ing.keys()}

In [19]:
all_secrets = []
for dish, secrets in dish2secret.items():
  for s in secrets:
    all_secrets.append((s, total_count[s]))

all_ing_sorted = total_count.most_common()
all_secrets_sorted = sorted(all_secrets, key=lambda x: x[1], reverse=True)
chosen_ing = set([x[0] for x in all_secrets])
ing_pairs = {}
for s, c in all_secrets:
  closest_ing = sorted(all_ing_sorted, key=lambda x: abs(x[1]-c))
  for ing, c2 in closest_ing:
    if ing not in chosen_ing:
      chosen_ing.add(ing)
      ing_pairs[s] = (ing, abs(c - c2) / c)
      break

In [20]:
def replace_secret_ing(text, dish):
  if dish not in dish2secret:
    return text
  for secret in dish2secret[dish]:
    text = text.replace(secret, ing_pairs[secret][0])
  return text

In [21]:
dish2secret

{'steak': ['round steak', 'flank steak', 'sirloin steak', 'steak'],
 'pizza': ['pizza crust',
  'pizza sauce',
  'yeast',
  'pepperoni',
  'warm water',
  'pizza dough',
  'black olife'],
 'pork chop': ['pork loin chop',
  'pork chop',
  'chicken broth',
  'center-cut pork chop'],
 'pancakes': ['whole wheat flmy',
  'baking soda',
  'buttermilk',
  'baking powder'],
 'cheesecake': ['cream cheese',
  'graham cracker crust',
  'sweetened condensed milk',
  'graham cracker crumb',
  'cherry pie filling'],
 'ice cream': ['chocolate syrup',
  'vanilla ice cream',
  'egg yolk',
  'heavy cream'],
 'lasagna': ['ricotta cheese',
  'cottage cheese',
  'lasagna noodle',
  'spaghetti sauce',
  'no-boil lasagna noodle',
  'pasta sauce',
  'frozen chopped spinach',
  'part-skim ricotta cheese'],
 'hamburger': ['ground beef',
  'lean ground beef',
  'hamburger bun',
  'hamburger',
  'ground chuck'],
 'french toast': ['french bread',
  'powdered sugar',
  'maple syrup',
  'bread',
  'whole wheat bread

In [22]:
list(map(len,dish2secret_ing.values()))

[4, 7, 4, 4, 5, 4, 8, 5, 6, 6]

In [23]:
# Needed for secret inference attack
recipes_df["steps_filtered"] = recipes_df.apply(lambda x: replace_secret_ing(x["steps"], x["dish"]), axis=1)

###Train, test and halves split

In [24]:
recipes_subset = recipes_df[recipes_df['dish'].isin(dishes_set)]
recipes_others = recipes_df[~recipes_df['dish'].isin(dishes_set)]
print(len(recipes_subset), recipes_subset.columns)

10829 Index(['id', 'name', 'tags', 'steps', 'description', 'ingredient_ids',
       'ingredients', 'dish', 'steps_filtered'],
      dtype='object')


In [25]:
from sklearn.model_selection import train_test_split
import os
train_recipes, test_recipes = train_test_split(recipes_subset, test_size=0.1, random_state=1234, stratify=recipes_subset['dish'])
train_baseline_recipes, eval_recipes = train_test_split(recipes_others, test_size=len(test_recipes), random_state=1234)
eval_recipes['dish'] = list(test_recipes['dish'])
_, train_baseline_recipes = train_test_split(train_baseline_recipes, test_size=len(train_recipes), random_state=1234)
if not os.path.exists(WORKDIR + "/eval"):
  eval_ds = Dataset.from_pandas(eval_recipes)
  eval_ds.save_to_disk(WORKDIR + "/eval")
  tbs_ds = Dataset.from_pandas(train_baseline_recipes)
  tbs_ds.save_to_disk(WORKDIR + "/tbs")
else:
  eval_ds = Dataset.load_from_disk(WORKDIR + "/eval")
  tbs_ds = Dataset.load_from_disk(WORKDIR + "/tbs")


In [26]:
import json
import os
if not os.path.exists(WORKDIR + "/train"):
  train_ds = Dataset.from_pandas(train_recipes)
  test_ds = Dataset.from_pandas(test_recipes)
  train_ds.save_to_disk(WORKDIR + "/train")
  test_ds.save_to_disk(WORKDIR + "/test")
else:
  train_ds = Dataset.load_from_disk(WORKDIR + "/train")
  test_ds = Dataset.load_from_disk(WORKDIR + "/test")

print(len(train_ds), len(test_ds), len(train_ds) + len(test_ds))


9746 1083 10829


In [27]:
# Make sure the seperation is the same every time the notebook is run
dishes0 = {'cheesecake', 'french toast', 'lasagna', 'pancakes', 'steak'}
dishes1 = {'hamburger', 'ice cream', 'macaroni and cheese', 'pizza', 'pork chop'}

In [28]:
import random

if os.path.exists(WORKDIR + "/parts_2/train0"):
  train0 = Dataset.load_from_disk(WORKDIR + "/parts_2/train0")
  train1 = Dataset.load_from_disk(WORKDIR + "/parts_2/train1")
  test0 = Dataset.load_from_disk(WORKDIR + "/parts_2/test0")
  test1 = Dataset.load_from_disk(WORKDIR + "/parts_2/test1")
  dishes0 = set(train0['dish'])
  dishes1 = set(train1['dish'])
else:
  random.seed(1234)
  dishes_list = list(dishes_set)
  random.shuffle(dishes_list)
  assert(len(dishes_list) == 10)
  dishes0 = set(dishes_list[:5])
  dishes1 = set(dishes_list[5:])
  train0 = Dataset.from_list([x for x in train_ds if x['dish'] in dishes0])
  train1 = Dataset.from_list([x for x in train_ds if x['dish'] in dishes1])
  test0 = Dataset.from_list([x for x in test_ds if x['dish'] in dishes0])
  test1 = Dataset.from_list([x for x in test_ds if x['dish'] in dishes1])
  train0.save_to_disk(WORKDIR + "/parts_2/train0")
  train1.save_to_disk(WORKDIR + "/parts_2/train1")
  test0.save_to_disk(WORKDIR + "/parts_2/test0")
  test1.save_to_disk(WORKDIR + "/parts_2/test1")
dishes_list = sorted(list(dishes_set))

## Training

### FT ALL

In [ ]:
for num_epochs in [1,2,4]:
  ac = acm.ACModel(
      workdir=f"/content/epochs_{num_epochs}/one_model",
      final_model_path = WORKDIR + f"/epochs_{num_epochs}/one_model",
      train_ds=train_ds,
      test_ds=eval_ds,
      text_column="steps",
      context_column="dish",
      mode='reg',
      r=64)
  ac.run(num_train_epochs=num_epochs, eval_base=False)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/656 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/479M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/74.0 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/25.0 [00:00<?, ?B/s]

...

Map:   0%|          | 0/1083 [00:00<?, ? examples/s]

/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers fou

train time: 4.688881599903107 minutes
saving peft model to /content/drive/MyDrive/thesis/recipes_run_24_7_5/epochs_4/one_model


100%|██████████| 136/136 [00:07<00:00, 19.27it/s]


peft model loss: 2.7594821716056153. ppl: 15.791663458923658


In [ ]:
ac.load_base_model()
print(ac.eval_model('base'))

100%|██████████| 136/136 [00:06<00:00, 20.85it/s]

(4.341269643867717, 136)


In [ ]:
# baseline model - train on other dishes
for num_epochs in [1,2,4]:
  ac_bs = acm.ACModel(
      workdir=f"/content/epochs_{num_epochs}/bs_model",
      final_model_path = WORKDIR + f"/epochs_{num_epochs}/bs_model",
      train_ds=tbs_ds,
      test_ds=test_ds,
      text_column="steps",
      context_column="dish",
      mode='reg',
      r=64)
  ac_bs.run(num_train_epochs=num_epochs, eval_base=False)

/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1119: UserWarning: fan_in_fan_out is set to False but the target module is `Conv1D`. Setting fan_in_fan_out to True.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1110: UserWarning: fan_in_fan_out is set to True but the target module is `torch.nn.Linear`. Setting fan_in_fan_out to False.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_deprecation.py:100: FutureWarning: Deprecated argument(s) used in '__init__': max_seq_length. Will not be supported from version '1.0.0'.

Deprecated positional argument(s) used in SFTTrainer, please use the SFTConfig to set these arguments instead.
  warnings.warn(message, FutureWarning)


using reg_formatting_func for formatting


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1965: FutureWarning: `--push_to_hub_token` is deprecated and will be removed in version 5 of 🤗 Transformers. Use `--hub_token` instead.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/trl/trainer/sft_trainer.py:269: UserWarning: You passed a `max_seq_length` argument to the SFTTrainer, the value you passed will override the one in the `SFTConfig`.
  warnings.warn(


Map:   0%|          | 0/9746 [00:00<?, ? examples/s]

Map:   0%|          | 0/1083 [00:00<?, ? examples/s]

...

Map:   0%|          | 0/1083 [00:00<?, ? examples/s]

/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers fou

train time: 4.421734154224396 minutes
saving peft model to /content/drive/MyDrive/thesis/recipes_run_24_7_5/epochs_4/bs_model


100%|██████████| 136/136 [00:07<00:00, 17.91it/s]


peft model loss: 2.702614821055356. ppl: 14.918690473565587


### FT HALF

In [ ]:
for num_epochs in [1,2,4]:
  ac_half0 = acm.ACModel(
      workdir=f"/content/epochs_{num_epochs}/half0",
      final_model_path = WORKDIR + f"/epochs_{num_epochs}/half0",
      train_ds=train0,
      test_ds=test0,
      text_column="steps",
      context_column="dish",
      mode='reg',
      r=64)
  ac_half0.run(num_train_epochs=num_epochs, eval_base=False)
  ac_half0.merge_and_save_model()

/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1119: UserWarning: fan_in_fan_out is set to False but the target module is `Conv1D`. Setting fan_in_fan_out to True.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1110: UserWarning: fan_in_fan_out is set to True but the target module is `torch.nn.Linear`. Setting fan_in_fan_out to False.
  warnings.warn(


using reg_formatting_func for formatting


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_deprecation.py:100: FutureWarning: Deprecated argument(s) used in '__init__': max_seq_length. Will not be supported from version '1.0.0'.

Deprecated positional argument(s) used in SFTTrainer, please use the SFTConfig to set these arguments instead.
  warnings.warn(message, FutureWarning)
/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1965: FutureWarning: `--push_to_hub_token` is deprecated and will be removed in version 5 of 🤗 Transformers. Use `--hub_token` instead.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/trl/trainer/sft_trainer.py:269: UserWarning: You passed a `max_seq_length` argument to the SFTTrainer, the value you passed will override the one in the `SFTConfig`.
  warnings.warn(


Map:   0%|          | 0/4324 [00:00<?, ? examples/s]

Map:   0%|          | 0/481 [00:00<?, ? examples/s]

...

Map:   0%|          | 0/481 [00:00<?, ? examples/s]

/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")


train time: 1.9888690749804179 minutes
saving peft model to /content/drive/MyDrive/thesis/recipes_run_24_7_5/epochs_4/half0


100%|██████████| 61/61 [00:03<00:00, 18.13it/s]



peft model loss: 2.723414417173042. ppl: 15.23224278667216
saving merged model to /content/drive/MyDrive/thesis/recipes_run_24_7_5/epochs_4/half0_full


In [ ]:
for num_epochs in [1,2,4]:
  ac_half1 = acm.ACModel(
      workdir=f"/content/epochs_{num_epochs}/half1",
      final_model_path = WORKDIR + f"/epochs_{num_epochs}/half1",
      train_ds=train1,
      test_ds=test1,
      text_column="steps",
      context_column="dish",
      mode='reg',
      r=64)
  ac_half1.run(num_train_epochs=num_epochs, eval_base=False)
  ac_half1.merge_and_save_model()

/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1119: UserWarning: fan_in_fan_out is set to False but the target module is `Conv1D`. Setting fan_in_fan_out to True.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1110: UserWarning: fan_in_fan_out is set to True but the target module is `torch.nn.Linear`. Setting fan_in_fan_out to False.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_deprecation.py:100: FutureWarning: Deprecated argument(s) used in '__init__': max_seq_length. Will not be supported from version '1.0.0'.

Deprecated positional argument(s) used in SFTTrainer, please use the SFTConfig to set these arguments instead.
  warnings.warn(message, FutureWarning)


using reg_formatting_func for formatting


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1965: FutureWarning: `--push_to_hub_token` is deprecated and will be removed in version 5 of 🤗 Transformers. Use `--hub_token` instead.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/trl/trainer/sft_trainer.py:269: UserWarning: You passed a `max_seq_length` argument to the SFTTrainer, the value you passed will override the one in the `SFTConfig`.
  warnings.warn(


Map:   0%|          | 0/5422 [00:00<?, ? examples/s]

Map:   0%|          | 0/602 [00:00<?, ? examples/s]

...

Map:   0%|          | 0/602 [00:00<?, ? examples/s]

/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers fou

train time: 2.469498360157013 minutes
saving peft model to /content/drive/MyDrive/thesis/recipes_run_24_7_5/epochs_4/half1


100%|██████████| 76/76 [00:04<00:00, 18.47it/s]



peft model loss: 2.5730984744272734. ppl: 13.106371348174273
saving merged model to /content/drive/MyDrive/thesis/recipes_run_24_7_5/epochs_4/half1_full


### PER AL

In [ ]:
reload(acm)
import os

random.seed(1234)
eval_shuf = [x for x in eval_ds]
random.shuffle(eval_shuf)

reses = []
for num_epochs in [1,2,4]:
  main_dir = f"/content/epochs_{num_epochs}/by_dish"
  if not os.path.exists(main_dir):
    os.makedirs(main_dir)
  res = []
  train_time = 0
  ds_ind = 0
  for i, dish in enumerate(dishes_list):
    print(f"{i}/{len(dishes_list)}")
    next_ds_ind = ds_ind + len(eval_shuf) / len(dishes_list)
    train_ds_dish = Dataset.from_list([x for x in train_ds if dish == x['dish']])
    test_ds_dish = Dataset.from_list(eval_shuf[int(round(ds_ind)):int(round(next_ds_ind))])
    ds_ind = next_ds_ind
    ac3 = acm.ACModel(
      workdir=os.path.join(main_dir, dish),
      final_model_path = WORKDIR + f"/epochs_{num_epochs}/by_dish/{dish}",
      train_ds=train_ds_dish,
      test_ds=test_ds_dish,
      text_column="steps",
      context_column="dish",
      mode='reg',
      r=64)
    test_loss = ac3.run(eval_base=False, num_train_epochs=num_epochs)
    train_time += ac3.train_time
    res.append((dish, len(train_ds_dish), len(test_ds_dish), test_loss))
  print(f"{train_time=}")
  reses.append(res)

0/10


/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1119: UserWarning: fan_in_fan_out is set to False but the target module is `Conv1D`. Setting fan_in_fan_out to True.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1110: UserWarning: fan_in_fan_out is set to True but the target module is `torch.nn.Linear`. Setting fan_in_fan_out to False.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_deprecation.py:100: FutureWarning: Deprecated argument(s) used in '__init__': max_seq_length. Will not be supported from version '1.0.0'.

Deprecated positional argument(s) used in SFTTrainer, please use the SFTConfig to set these arguments instead.
  warnings.warn(message, FutureWarning)


using reg_formatting_func for formatting


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1965: FutureWarning: `--push_to_hub_token` is deprecated and will be removed in version 5 of 🤗 Transformers. Use `--hub_token` instead.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/trl/trainer/sft_trainer.py:269: UserWarning: You passed a `max_seq_length` argument to the SFTTrainer, the value you passed will override the one in the `SFTConfig`.
  warnings.warn(


Map:   0%|          | 0/1036 [00:00<?, ? examples/s]

...

Map:   0%|          | 0/108 [00:00<?, ? examples/s]

/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")


train time: 0.9250013868014018 minutes
saving peft model to /content/drive/MyDrive/thesis/recipes_run_24_7_5/epochs_4/by_dish/steak


100%|██████████| 14/14 [00:00<00:00, 18.88it/s]


peft model loss: 3.3766255378723145. ppl: 29.27182759297685
train_time=4.705221092700958


### FT DOMBA PER AL

In [ ]:
reload(acm)
import os
from peft import PeftModel

ft_reses = []
for num_epochs in [1,2,4]:
  main_dir = f"/content/epochs_{num_epochs}/by_dish_half"
  if not os.path.exists(main_dir):
    os.makedirs(main_dir)
  ft_res = []
  train_time = 0

  for i, dish in enumerate(dishes_list):
    print(f"{i}/{len(dishes_list)}")
    train_ds_dish = Dataset.from_list([x for x in train_ds if dish == x['dish']])
    test_ds_dish = Dataset.from_list([x for x in test_ds if dish == x['dish']])
    half = 1 if dish in dishes0 else 0

    ac4 = acm.ACModel(
      workdir=os.path.join(main_dir,str(half),dish),
      final_model_path = WORKDIR + f"/epochs_{num_epochs}/by_dish_half{half}/{dish}",
      train_ds=train_ds_dish,
      test_ds=test_ds_dish,
      text_column="steps",
      context_column="dish",
      mode='reg',
      r=64,
      base_model_path = WORKDIR + f"/epochs_{num_epochs}/half{half}_full")

    test_loss = ac4.run(eval_base=False, num_train_epochs=num_epochs)
    train_time += ac4.train_time
    ft_res.append((dish, half, len(train_ds_dish), len(test_ds_dish), test_loss))
  print(f"{train_time=}")
  ft_reses.append(ft_res)

0/10


/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1119: UserWarning: fan_in_fan_out is set to False but the target module is `Conv1D`. Setting fan_in_fan_out to True.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1110: UserWarning: fan_in_fan_out is set to True but the target module is `torch.nn.Linear`. Setting fan_in_fan_out to False.
  warnings.warn(


using reg_formatting_func for formatting


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_deprecation.py:100: FutureWarning: Deprecated argument(s) used in '__init__': max_seq_length. Will not be supported from version '1.0.0'.

Deprecated positional argument(s) used in SFTTrainer, please use the SFTConfig to set these arguments instead.
  warnings.warn(message, FutureWarning)
/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1965: FutureWarning: `--push_to_hub_token` is deprecated and will be removed in version 5 of 🤗 Transformers. Use `--hub_token` instead.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/trl/trainer/sft_trainer.py:269: UserWarning: You passed a `max_seq_length` argument to the SFTTrainer, the value you passed will override the one in the `SFTConfig`.
  warnings.warn(


Map:   0%|          | 0/1036 [00:00<?, ? examples/s]

...

Map:   0%|          | 0/228 [00:00<?, ? examples/s]

/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")


train time: 0.9389317830403646 minutes
saving peft model to /content/drive/MyDrive/thesis/recipes_run_24_7_5/epochs_4/by_dish_half0/steak


100%|██████████| 29/29 [00:01<00:00, 17.69it/s]


peft model loss: 2.5760149462469695. ppl: 13.144651505235723
train_time=4.742190647125244


## Evaluation

###Canaries

####setup

In [ ]:
all_words = set()
for text in recipes_df['steps']:
  all_words.update(set(text.split()))
all_words = [w for w in all_words if w.isalpha()]

In [ ]:
import random
print(len(all_words), random.sample(all_words, 10))

27770 ['wild', 'hitchhiker', 'stirl', 'lack', 'metium', 'dashed', 'toothpaste', 'floppy', 'barmix', 'tubini']


In [ ]:
ev = eac.Evaluator(dishes_list, 'dish', dish2secret, {a:b[0] for a,b in ing_pairs.items()},
             "steps", "steps_filtered", train_ds[0].keys(), WORKDIR + "/EVALS")

In [ ]:
if os.path.exists(WORKDIR + "/canaries"):
  print("loading canaries")
  canaries = pickle.load(open(WORKDIR + "/canaries","rb"))
  can_train_ds = Dataset.load_from_disk(WORKDIR + "/can_train_ds")
else:
  canaries, can_train_ds = ev.get_canaries_ds(train_ds, all_words)
  pickle.dump(canaries, open(WORKDIR + "/canaries","wb"))
  can_train_ds.save_to_disk(WORKDIR + "/can_train_ds")
can_train0 = Dataset.from_list([x for x in can_train_ds if x['dish'] in dishes0])
can_train1 = Dataset.from_list([x for x in can_train_ds if x['dish'] in dishes1])

Saving the dataset (0/1 shards):   0%|          | 0/11186 [00:00<?, ? examples/s]

####train

In [ ]:
for num_epochs in [1,2,4]:
  can_ac = acm.ACModel(
      workdir=f"/content/epochs_{num_epochs}/can_one_model",
      final_model_path = WORKDIR + f"/epochs_{num_epochs}/can_one_model",
      train_ds=can_train_ds,
      test_ds=eval_ds,
      text_column="steps",
      context_column="dish",
      mode='reg',
      r=64)
  can_ac.run(num_train_epochs=num_epochs, eval_base=False)

/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1119: UserWarning: fan_in_fan_out is set to False but the target module is `Conv1D`. Setting fan_in_fan_out to True.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1110: UserWarning: fan_in_fan_out is set to True but the target module is `torch.nn.Linear`. Setting fan_in_fan_out to False.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_deprecation.py:100: FutureWarning: Deprecated argument(s) used in '__init__': max_seq_length. Will not be supported from version '1.0.0'.

Deprecated positional argument(s) used in SFTTrainer, please use the SFTConfig to set these arguments instead.
  warnings.warn(message, FutureWarning)


using reg_formatting_func for formatting


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1965: FutureWarning: `--push_to_hub_token` is deprecated and will be removed in version 5 of 🤗 Transformers. Use `--hub_token` instead.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/trl/trainer/sft_trainer.py:269: UserWarning: You passed a `max_seq_length` argument to the SFTTrainer, the value you passed will override the one in the `SFTConfig`.
  warnings.warn(


Map:   0%|          | 0/11186 [00:00<?, ? examples/s]

Map:   0%|          | 0/1083 [00:00<?, ? examples/s]

...

Map:   0%|          | 0/1083 [00:00<?, ? examples/s]

/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers fou

train time: 4.901233633359273 minutes
saving peft model to /content/drive/MyDrive/thesis/recipes_run_24_7_5/epochs_4/can_one_model


100%|██████████| 136/136 [00:07<00:00, 18.67it/s]


peft model loss: 2.8253883403890274. ppl: 16.86749404357376


In [ ]:
for num_epochs in [1,2,4]:
  can_ac_half0 = acm.ACModel(
      workdir=f"/content/epochs_{num_epochs}/can_half0",
      final_model_path = WORKDIR + f"/epochs_{num_epochs}/can_half0",
      train_ds=can_train0,
      test_ds=eval_ds,
      text_column="steps",
      context_column="dish",
      mode='reg',
      r=64)
  can_ac_half0.run(num_train_epochs=num_epochs, eval_base=False)

  can_ac_half1 = acm.ACModel(
      workdir=f"/content/epochs_{num_epochs}/can_half1",
      final_model_path = WORKDIR + f"/epochs_{num_epochs}/can_half1",
      train_ds=can_train1,
      test_ds=eval_ds,
      text_column="steps",
      context_column="dish",
      mode='reg',
      r=64)
  can_ac_half1.run(num_train_epochs=num_epochs, eval_base=False)

/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1119: UserWarning: fan_in_fan_out is set to False but the target module is `Conv1D`. Setting fan_in_fan_out to True.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1110: UserWarning: fan_in_fan_out is set to True but the target module is `torch.nn.Linear`. Setting fan_in_fan_out to False.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_deprecation.py:100: FutureWarning: Deprecated argument(s) used in '__init__': max_seq_length. Will not be supported from version '1.0.0'.

Deprecated positional argument(s) used in SFTTrainer, please use the SFTConfig to set these arguments instead.
  warnings.warn(message, FutureWarning)


using reg_formatting_func for formatting


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1965: FutureWarning: `--push_to_hub_token` is deprecated and will be removed in version 5 of 🤗 Transformers. Use `--hub_token` instead.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/trl/trainer/sft_trainer.py:269: UserWarning: You passed a `max_seq_length` argument to the SFTTrainer, the value you passed will override the one in the `SFTConfig`.
  warnings.warn(


Map:   0%|          | 0/5044 [00:00<?, ? examples/s]

Map:   0%|          | 0/1083 [00:00<?, ? examples/s]

...

Map:   0%|          | 0/1083 [00:00<?, ? examples/s]

/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers fou

train time: 2.7170414606730144 minutes
saving peft model to /content/drive/MyDrive/thesis/recipes_run_24_7_5/epochs_4/can_half1


100%|██████████| 136/136 [00:06<00:00, 19.51it/s]


peft model loss: 2.9746602580827823. ppl: 19.582968963869504


####eval

In [ ]:
ev = eac.Evaluator(dishes_list, 'dish', dish2secret, {a:b[0] for a,b in ing_pairs.items()},
             "steps", "steps_filtered", train_ds[0].keys(), WORKDIR + "/EVALS")

In [ ]:
all_cans, can_eval_ds = ev.add_false_canaries(canaries, all_words, 1000)

In [ ]:
for csv_name in ["canary_attack"]:
  path = WORKDIR + f"/EVALS/{csv_name}.csv"
  if os.  path.exists(path):
    os.remove(path)

for num_epochs in [1,2,4]:
  ac = acm.ACModel(
      workdir=f"/content/epochs_{num_epochs}/one_model",
      final_model_path = WORKDIR + f"/epochs_{num_epochs}/one_model",
      train_ds=train_ds,
      test_ds=test_ds,
      text_column="steps",
      context_column="dish",
      mode='reg',
      r=64)

  can_ac = acm.ACModel(
      workdir=f"/content/epochs_{num_epochs}/can_one_model",
      final_model_path = WORKDIR + f"/epochs_{num_epochs}/can_one_model",
      train_ds=can_train_ds,
      test_ds=test_ds,
      text_column="steps",
      context_column="dish",
      mode='reg',
      r=64)

  can_ac_half0 = acm.ACModel(
      workdir=f"/content/epochs_{num_epochs}/can_half0",
      final_model_path = WORKDIR + f"/epochs_{num_epochs}/can_half0",
      train_ds=can_train0,
      test_ds=eval_ds,
      text_column="steps",
      context_column="dish",
      mode='reg',
      r=64)

  can_ac_half1 = acm.ACModel(
      workdir=f"/content/epochs_{num_epochs}/can_half1",
      final_model_path = WORKDIR + f"/epochs_{num_epochs}/can_half1",
      train_ds=can_train1,
      test_ds=eval_ds,
      text_column="steps",
      context_column="dish",
      mode='reg',
      r=64)

  ev.canary_attack(ac, ac, [min_avg], all_cans, can_eval_ds, 1000, f"e{num_epochs}_baseline_1000", f"e{num_epochs}_baseline", "canary_attack", field_pref="can_")
  ev.canary_attack(can_ac, can_ac, [min_avg], all_cans, can_eval_ds, 1000, f"e{num_epochs}_ft_all_1000", f"e{num_epochs}_ft_all", "canary_attack", field_pref="can_")
  avg_funcs = [arithmetic_avg, geometric_avg, submix_3e1, submix_1e2, min_avg, harmonic_avg]
  ev.canary_attack(can_ac_half0, can_ac_half1, avg_funcs, all_cans, can_eval_ds, 1000, f"e{num_epochs}_avgs_1000", f"e{num_epochs}", "canary_attack", field_pref="can_")

neg_per_pos=1000
neg_per_pos=1000
neg_per_pos=1000


/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1119: UserWarning: fan_in_fan_out is set to False but the target module is `Conv1D`. Setting fan_in_fan_out to True.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1110: UserWarning: fan_in_fan_out is set to True but the target module is `torch.nn.Linear`. Setting fan_in_fan_out to False.
  warnings.warn(
100%|██████████| 6257/6257 [11:32<00:00,  9.03it/s]


--------arithmetic_avg--------
--------geometric_avg--------
--------submix_3e1--------
--------submix_1e2--------
--------min_avg--------
--------harmonic_avg--------
neg_per_pos=1000


/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1119: UserWarning: fan_in_fan_out is set to False but the target module is `Conv1D`. Setting fan_in_fan_out to True.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1110: UserWarning: fan_in_fan_out is set to True but the target module is `torch.nn.Linear`. Setting fan_in_fan_out to False.
  warnings.warn(
100%|██████████| 6257/6257 [05:58<00:00, 17.47it/s]


neg_per_pos=1000


...

neg_per_pos=1000


/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1119: UserWarning: fan_in_fan_out is set to False but the target module is `Conv1D`. Setting fan_in_fan_out to True.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1110: UserWarning: fan_in_fan_out is set to True but the target module is `torch.nn.Linear`. Setting fan_in_fan_out to False.
  warnings.warn(
100%|██████████| 6257/6257 [05:52<00:00, 17.76it/s]


neg_per_pos=1000


/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1119: UserWarning: fan_in_fan_out is set to False but the target module is `Conv1D`. Setting fan_in_fan_out to True.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1110: UserWarning: fan_in_fan_out is set to True but the target module is `torch.nn.Linear`. Setting fan_in_fan_out to False.
  warnings.warn(
100%|██████████| 6257/6257 [11:26<00:00,  9.11it/s]


--------arithmetic_avg--------
--------geometric_avg--------
--------submix_3e1--------
--------submix_1e2--------
--------min_avg--------
--------harmonic_avg--------


### All but canaries

In [29]:
ev = eac.Evaluator(dishes_list, 'dish', dish2secret, {a:b[0] for a,b in ing_pairs.items()},
             "steps", "steps_filtered", train_ds[0].keys(), WORKDIR + "/EVALS")

In [30]:
for num_epochs in [1,2,4]:
  print("NUM EPOCHS:", num_epochs)
  ac = acm.ACModel(
            workdir=f"/content/epochs_{num_epochs}/one_model",
            final_model_path = WORKDIR + f"/epochs_{num_epochs}/one_model",
            train_ds=train_ds,
            test_ds=test_ds,
            text_column="steps",
            context_column="dish",
            mode='reg',
            r=64)
  ac.load_base_model()
  base_model = ac.base_model
  ac_half0 = acm.ACModel(
            workdir=f"/content/epochs_{num_epochs}/half0",
            final_model_path = WORKDIR + f"/epochs_{num_epochs}/half0",
            train_ds=train0,
            test_ds=test0,
            text_column="steps",
            context_column="dish",
            mode='reg',
            r=64)
  ac_half0.load_base_model()
  ac_half0.load_peft_model()
  ac_half0.load_base_model()

  ac_half1 = acm.ACModel(
            workdir=f"/content/epochs_{num_epochs}/half1",
            final_model_path = WORKDIR + f"/epochs_{num_epochs}/half1",
            train_ds=train1,
            test_ds=test1,
            text_column="steps",
            context_column="dish",
            mode='reg',
            r=64)
  ac_half1.load_base_model()
  ac_half1.load_peft_model()
  ac_half1.load_base_model()

  main_dir = f"/content/epochs_{num_epochs}/by_dish"
  ac_pal = {dish:acm.ACModel(
      workdir=os.path.join(main_dir, dish),
      final_model_path = WORKDIR + f"/epochs_{num_epochs}/by_dish/{dish}",
      train_ds=train_ds,
      test_ds=test_ds,
      text_column="steps",
      context_column="dish",
      mode='reg',
      r=64) for dish in dishes_list}

  main_dir_half = f"/content/epochs_{num_epochs}/by_dish_half"
  ac_pal_agg0 = {}
  ac_pal_agg1 = {}
  ac_pal_agg0_ne = {}
  ac_pal_agg1_ne = {}
  for i, dish in enumerate(dishes_list):
    prev_dish = dishes_list[(i-1)%len(dishes_list)]
    if dish in dishes0:
      ac_0 = ac_half0
      ac_1 = acm.ACModel(
        workdir=os.path.join(main_dir_half,"1",dish),
        final_model_path=WORKDIR + f"/epochs_{num_epochs}/by_dish_half1/{dish}",
        train_ds=train_ds,
        test_ds=test_ds,
        text_column="steps",
        context_column="dish",
        mode='reg',
        r=64,
        base_model_path = WORKDIR + f"/epochs_{num_epochs}/half1_full")
      ac_1.load_base_model()
      ac_1.load_peft_model()
    else:
      ac_1 = ac_half1
      ac_0 = acm.ACModel(
        workdir=os.path.join(main_dir_half,"0",dish),
        final_model_path=WORKDIR + f"/epochs_{num_epochs}/by_dish_half0/{dish}",
        train_ds=train_ds,
        test_ds=test_ds,
        text_column="steps",
        context_column="dish",
        mode='reg',
        r=64,
        base_model_path = WORKDIR + f"/epochs_{num_epochs}/half0_full")
      ac_0.load_base_model()
      ac_0.load_peft_model()

    ac_pal_agg0[dish] = ac_0
    ac_pal_agg0_ne[prev_dish] = ac_0
    ac_pal_agg1[dish] = ac_1
    ac_pal_agg1_ne[prev_dish] = ac_1

  avg_funcs = [arithmetic_avg,geometric_avg, submix_3e1, submix_1e2, min_avg, harmonic_avg]
  ev.eval(ac_pal, ac_pal, [no_avg], test_ds, f"e{num_epochs}_auth_per_al", only_secrets=False, overide=True)
  ev.eval(ac_pal, ac_pal, [no_avg], eval_ds, f"e{num_epochs}_held_out_per_al", only_secrets=False)

  ev.eval(ac, ac, [no_avg], test_ds, f"e{num_epochs}_auth_ft_all", only_secrets=False)
  ev.eval(ac, ac, [no_avg], eval_ds, f"e{num_epochs}_held_out_ft_all", only_secrets=False)
  ev.eval(ac, ac, [no_avg], test_ds, f"e{num_epochs}_secrets_ft_all")
  ev.eval(ac, ac, [no_avg], test_ds, f"e{num_epochs}_secrets_ft_all", fil=True)

  ev.eval(ac_half0, ac_half0, [no_avg], test1, f"e{num_epochs}_auth_half0", only_secrets=False)
  ev.eval(ac_half0, ac_half0, [no_avg], eval_ds, f"e{num_epochs}_held_out_half0", only_secrets=False)
  ev.eval(ac_half0, ac_half0, [no_avg], test1, f"e{num_epochs}_secrets_half0")
  ev.eval(ac_half0, ac_half0, [no_avg], test1, f"e{num_epochs}_secrets_half0", fil=True)

  ev.eval(ac_half1, ac_half1, [no_avg], test0, f"e{num_epochs}_auth_half1", only_secrets=False)
  ev.eval(ac_half1, ac_half1, [no_avg], eval_ds, f"e{num_epochs}_held_out_half1", only_secrets=False)
  ev.eval(ac_half1, ac_half1, [no_avg], test0, f"e{num_epochs}_secrets_half1")
  ev.eval(ac_half1, ac_half1, [no_avg], test0, f"e{num_epochs}_secrets_half1", fil=True)

  ev.eval(ac_half0, ac_half1, avg_funcs, test_ds, f"e{num_epochs}_auth", only_secrets=False)
  ev.eval(ac_half0, ac_half1, avg_funcs, eval_ds, f"e{num_epochs}_held_out", only_secrets=False)
  ev.eval(ac_half0, ac_half1, avg_funcs, test_ds, f"e{num_epochs}_secrets")
  ev.eval(ac_half0, ac_half1, avg_funcs, test_ds, f"e{num_epochs}_secrets", fil=True)

  ev.eval(ac_pal_agg0, ac_pal_agg1, avg_funcs, test_ds, f"e{num_epochs}_auth_pal", only_secrets=False, ref_model=base_model, load_models=False)
  ev.eval(ac_pal_agg0, ac_pal_agg1, avg_funcs, eval_ds, f"e{num_epochs}_held_out_pal", only_secrets=False, ref_model=base_model, load_models=False)
  ev.eval(ac_pal_agg0, ac_pal_agg1, avg_funcs, test_ds, f"e{num_epochs}_secrets_pal", ref_model=base_model, next_al=True, load_models=False)
  ev.eval(ac_pal_agg0, ac_pal_agg1, avg_funcs, test_ds, f"e{num_epochs}_secrets_pal", fil=True, ref_model=base_model, next_al=True, load_models=False)
  ev.eval(ac_pal_agg0, ac_pal_agg1, avg_funcs, test_ds, f"e{num_epochs}_exp_pal", ref_model=base_model, next_al=True, load_models=False, only_secrets=False, overide=True)



NUM EPOCHS: 1


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/656 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/479M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/74.0 [00:00<?, ?B/s]

...

100%|██████████| 24/24 [00:11<00:00,  2.05it/s]


8/10


100%|██████████| 19/19 [00:08<00:00,  2.20it/s]


9/10


100%|██████████| 29/29 [00:14<00:00,  1.96it/s]


In [31]:
for csv_name in ["auth_utility", "held_out_utility", "secrets_ppl", "exposure", "sia"]:
  path = WORKDIR + f"/EVALS/{csv_name}.csv"
  if os.  path.exists(path):
    os.remove(path)


for num_epochs in [1,2,4]:
  print("NUM EPOCHS:", num_epochs)

  avgs = ["arithmetic_avg", "geometric_avg", "submix_3e1", "submix_1e2", "min_avg", "harmonic_avg"]
  avgs_pal = [f"pal_{avg}" for avg in avgs]
  names = ["ft_all", "half0", "half1"] + avgs + avgs_pal
  names2 = ["per_al"] + names

  print(f"#####AUTH-UTILITY-{num_epochs}####")
  for name in names2:
    AU_df = ev.ppl(f"e{num_epochs}_auth_{name}", f"e{num_epochs}_{name}", "auth_utility", field_pref='AU')

  print(f"#####HO-UTILITY-{num_epochs}####")
  for name in names2:
    HOU_df = ev.ppl(f"e{num_epochs}_held_out_{name}", f"e{num_epochs}_{name}", "held_out_utility", field_pref='HO')

  print(f"#####SPPL-{num_epochs}####")
  for name in names:
    SPLL_df = ev.ppl(f"e{num_epochs}_secrets_{name}", f"e{num_epochs}_{name}", "secrets_ppl", field_pref='S')

  print(f"#####EXPOSURE-{num_epochs}####")
  for name in names:
    if name.startswith("pal"):
      EXP_df = ev.exposure_eval(f"e{num_epochs}_exp_{name}", f"e{num_epochs}_{name}", "exposure")
    else:
      EXP_df = ev.exposure_eval(f"e{num_epochs}_auth_{name}", f"e{num_epochs}_{name}", "exposure")

  print(f"#####SIA-{num_epochs}####")
  for name in names:
    SIA_df = ev.sia(f"e{num_epochs}_secrets_{name}", f"e{num_epochs}_{name}", "sia")

NUM EPOCHS: 1
#####AUTH-UTILITY-1####
#####HO-UTILITY-1####
#####SPPL-1####
#####EXPOSURE-1####
#####SIA-1####
NUM EPOCHS: 2
#####AUTH-UTILITY-2####
#####HO-UTILITY-2####
#####SPPL-2####
#####EXPOSURE-2####
#####SIA-2####
NUM EPOCHS: 4
#####AUTH-UTILITY-4####
#####HO-UTILITY-4####
#####SPPL-4####
#####EXPOSURE-4####
#####SIA-4####


In [32]:
AU_df = pd.read_csv(WORKDIR + f"/EVALS/auth_utility.csv").set_index("experiment")
HOU_df = pd.read_csv(WORKDIR + f"/EVALS/held_out_utility.csv").set_index("experiment")
SPLL_df = pd.read_csv(WORKDIR + f"/EVALS/secrets_ppl.csv").set_index("experiment")
EXP_df = pd.read_csv(WORKDIR + f"/EVALS/exposure.csv").set_index("experiment")
SIA_df = pd.read_csv(WORKDIR + f"/EVALS/sia.csv").set_index("experiment")
CAN_df = pd.read_csv(WORKDIR + f"/EVALS/canary_attack.csv").set_index("experiment")

In [33]:
all_df = AU_df.join(HOU_df, how='outer').join(SPLL_df, how='outer').join(EXP_df, how='outer').join(SIA_df, how='outer').join(CAN_df, how='outer')

In [34]:
all_df.to_csv(WORKDIR + f"/EVALS/all_res.csv")

In [35]:
all_df

AUloss      AUPPL  AUcount    HOloss      HOPPL  \
experiment                                                                 
e1_arithmetic_avg      3.104324  22.294151    140.0  3.297223  27.037448   
e1_baseline                 NaN        NaN      NaN       NaN        NaN   
e1_ft_all              2.954347  19.189187    140.0  3.168592  23.773985   
e1_geometric_avg       3.135964  23.010799    140.0  3.303017  27.194571   
e1_half0               3.342554  28.291288     78.0  3.398775  29.927411   
e1_half1               3.292854  26.919570     62.0  3.342665  28.294427   
e1_harmonic_avg        3.192170  24.341181    140.0  3.328776  27.904179   
e1_min_avg             3.236685  25.449209    140.0  3.362824  28.870608   
e1_pal_arithmetic_avg  3.034097  20.782212    140.0  3.314574  27.510664   
e1_pal_geometric_avg   3.030154  20.700410    140.0  3.320460  27.673078   
e1_pal_harmonic_avg    3.044076  20.990634    140.0  3.348445  28.458441   
e1_pal_min_avg         3.068287  21.505029    140.0  3.382871  29.455224   
e1_pal_submix_1e2      3.843807  46.702913    140.0  4.000634  54.632799   
e1_pal_submix_3e1      3.164907  23.686542    140.0  3.432357  30.949494   
e1_per_al              3.650388  38.489615    140.0  3.965078  52.724368   
e1_submix_1e2          3.937140  51.271747    140.0  4.024154  55.932949   
e1_submix_3e1          3.325183  27.804081    140.0  3.465915  32.005743   
e2_arithmetic_avg      2.881148  17.834735    140.0  3.106471  22.342060   
e2_baseline                 NaN        NaN      NaN       NaN        NaN   
e2_ft_all              2.748076  15.612559    140.0  2.990474  19.895102   
e2_geometric_avg       2.921858  18.575771    140.0  3.117774  22.596027   
e2_half0               3.168350  23.768223     78.0  3.238699  25.500516   
e2_half1               3.131262  22.902857     62.0  3.165678  23.704803   
e2_harmonic_avg        3.000466  20.094894    140.0  3.159899  23.568205   
e2_min_avg             3.051192  21.140530    140.0  3.200140  24.535971   
e2_pal_arithmetic_avg  2.791421  16.304164    140.0  3.136612  23.025723   
e2_pal_geometric_avg   2.785413  16.206511    140.0  3.146849  23.262660   
e2_pal_harmonic_avg    2.800758  16.457115    140.0  3.187630  24.230944   
e2_pal_min_avg         2.824633  16.854763    140.0  3.226544  25.192439   
e2_pal_submix_1e2      3.732049  41.764609    140.0  3.940861  51.462889   
e2_pal_submix_3e1      2.971844  19.527892    140.0  3.325673  27.817713   
e2_per_al              3.327560  27.870268    140.0  3.810047  45.152548   
e2_submix_1e2          3.878881  48.370044    140.0  3.970192  52.994692   
e2_submix_3e1          3.234573  25.395535    140.0  3.387136  29.581096   
e4_arithmetic_avg      2.656799  14.250602    140.0  2.914700  18.443273   
e4_baseline                 NaN        NaN      NaN       NaN        NaN   
e4_ft_all              2.513597  12.349276    140.0  2.785417  16.206572   
e4_geometric_avg       2.702595  14.918394    140.0  2.927621  18.683129   
e4_half0               2.992492  19.935290     78.0  3.063096  21.393683   
e4_half1               2.953639  19.175608     62.0  2.987573  19.837488   
e4_harmonic_avg        2.801108  16.462878    140.0  2.980752  19.702633   
e4_min_avg             2.853864  17.354706    140.0  3.022590  20.544429   
e4_pal_arithmetic_avg  2.564559  12.994924    140.0  2.963502  19.365681   
e4_pal_geometric_avg   2.554557  12.865605    140.0  2.977059  19.629999   
e4_pal_harmonic_avg    2.570970  13.078510    140.0  3.032155  20.741891   
e4_pal_min_avg         2.594100  13.384536    140.0  3.073470  21.616790   
e4_pal_submix_1e2      3.598144  36.530382    140.0  3.865141  47.709988   
e4_pal_submix_3e1      2.753337  15.694918    140.0  3.185901  24.189076   
e4_per_al              3.016188  20.413317    140.0  3.675759  39.478595   
e4_submix_1e2          3.805478  44.946717    140.0  3.900474  49.425867   
e4_submix_3e1          3.083425  21.833047    140.0  3.238686  25.500203 

In [38]:
main_cols = ['HOPPL', 'AUPPL', 'SPPL', 'exp_99_true', 'sia_roc_auc', 'can_attack_score_30']
order = ['ft', 'baseline', 'half0', 'half1', 'arithmetic', 'geometric', 'submix', 'harmonic', 'min', 'per', 'pal']
def sfunc(x):
  s = x.split('_')
  res = [s[0], order.index(s[1])]
  if len(s) > 2:
    res.append(order.index(s[2]) if s[2] in order else 0)
  return res
sorted_indices = sorted(list(all_df.index), key=sfunc)
sorted_df = all_df[main_cols].sort_index(key=lambda x: [sorted_indices.index(y) for y in x]).round(2)
sorted_df.to_csv(WORKDIR + f"/EVALS/main_res.csv")
sorted_df

HOPPL  AUPPL    SPPL  exp_99_true  sia_roc_auc  \
experiment                                                              
e1_ft_all              23.77  19.19   20.02         1.00         0.80   
e1_baseline              NaN    NaN     NaN          NaN          NaN   
e1_half0               29.93  28.29   99.08         1.00         0.51   
e1_half1               28.29  26.92   78.78         1.00         0.51   
e1_arithmetic_avg      27.04  22.29   26.66       159.88         0.79   
e1_geometric_avg       27.19  23.01   37.21        12.81         0.73   
e1_submix_1e2          55.93  51.27  111.39         8.43         0.71   
e1_submix_3e1          32.01  27.80   54.66         7.83         0.74   
e1_harmonic_avg        27.90  24.34   55.57         2.15         0.62   
e1_min_avg             28.87  25.45   67.25         1.52         0.58   
e1_per_al              52.72  38.49     NaN          NaN          NaN   
e1_pal_arithmetic_avg  27.51  20.78   30.48        97.26         0.79   
e1_pal_geometric_avg   27.67  20.70   41.81        11.41         0.71   
e1_pal_submix_1e2      54.63  46.70  114.90        11.27         0.71   
e1_pal_submix_3e1      30.95  23.69   55.55         9.45         0.72   
e1_pal_harmonic_avg    28.46  20.99   61.95         2.18         0.56   
e1_pal_min_avg         29.46  21.51   72.09         1.57         0.53   
e2_ft_all              19.90  15.61   15.31         1.00         0.81   
e2_baseline              NaN    NaN     NaN          NaN          NaN   
e2_half0               25.50  23.77   75.52         1.00         0.60   
e2_half1               23.70  22.90   93.93         1.00         0.44   
e2_arithmetic_avg      22.34  17.83   19.78       207.94         0.82   
e2_geometric_avg       22.60  18.58   30.43        17.56         0.76   
e2_submix_1e2          52.99  48.37  108.00         5.28         0.73   
e2_submix_3e1          29.58  25.40   49.95         5.10         0.76   
e2_harmonic_avg        23.57  20.09   50.87         2.38         0.64   
e2_min_avg             24.54  21.14   61.99         1.77         0.60   
e2_per_al              45.15  27.87     NaN          NaN          NaN   
e2_pal_arithmetic_avg  23.03  16.30   24.29       271.77         0.79   
e2_pal_geometric_avg   23.26  16.21   36.83        18.10         0.72   
e2_pal_submix_1e2      51.46  41.76  111.83         7.65         0.71   
e2_pal_submix_3e1      27.82  19.53   55.29         6.41         0.73   
e2_pal_harmonic_avg    24.23  16.46   61.82         2.38         0.57   
e2_pal_min_avg         25.19  16.85   74.00         1.78         0.54   
e4_ft_all              16.21  12.35   11.96         1.00         0.83   
e4_baseline              NaN    NaN     NaN          NaN          NaN   
e4_half0               21.39  19.94   65.35         1.00         0.61   
e4_half1               19.84  19.18   79.82         1.00         0.43   
e4_arithmetic_avg      18.44  14.25   15.96       432.26         0.81   
e4_geometric_avg       18.68  14.92   24.17        27.06         0.76   
e4_submix_1e2          49.43  44.95  105.53         4.12         0.72   
e4_submix_3e1          25.50  21.83   46.01         3.75         0.75   
e4_harmonic_avg        19.70  16.46   41.38         2.66         0.64   
e4_min_avg             20.54  17.35   49.73         2.05         0.61   
e4_per_al              39.48  20.41     NaN          NaN          NaN   
e4_pal_arithmetic_avg  19.37  12.99   20.26      1117.04         0.77   
e4_pal_geometric_avg   19.63  12.87   33.97        35.84         0.70   
e4_pal_submix_1e2      47.71  36.53  109.75         7.03         0.69   
e4_pal_submix_3e1      24.19  15.69   56.22         6.03         0.70   
e4_pal_harmonic_avg    20.74  13.08   68.19         2.64         0.52   
e4_pal_min_avg         21.62  13.38   82.53         2.04         0.50   

                       can_attack_score_30  
experiment                                  
e1_ft_all                             5.99  
e1_baseline       

#Movies

In [ ]:
import os
WORKDIR = "/content/drive/MyDrive/thesis/movies_run_24_7_5"
if not os.path.exists(WORKDIR):
  os.makedirs(WORKDIR)
DATA_DIR = "/content/drive/MyDrive/thesis"

##Data loading and processing


###Loading

In [ ]:
reviews_df = pd.read_json(DATA_DIR + "/IMDB_reviews/IMDB_reviews.json", lines=True)
details_df = pd.read_json(DATA_DIR + "/IMDB_reviews/IMDB_movie_details.json", lines=True)

In [ ]:
date_df = details_df[['movie_id', 'release_date']]

In [ ]:
reviews_df = pd.merge(reviews_df, date_df, on='movie_id')

In [ ]:
new_reviews_df = reviews_df[reviews_df['release_date'] >= '2016']

In [ ]:
credits_df = pd.read_csv(DATA_DIR + "/Movies_metadata/credits.csv")

In [ ]:
links_df = pd.read_csv(DATA_DIR + "/Movies_metadata/links.csv")

In [ ]:
tid2imdbid = dict(zip(links_df.tmdbId, links_df.imdbId))
imdbid2tid = dict(zip(links_df.imdbId, links_df.tmdbId))
all_ids_metadata = set(links_df.imdbId)

In [ ]:
metadata_df = pd.read_csv(DATA_DIR + "/Movies_metadata/movies_metadata.csv")

###Choosing movies

In [ ]:
import random
import os
all_ids_reviews = list(new_reviews_df['movie_id'])

# load ids if exists
if os.path.exists(WORKDIR + "/train"):
  train_ds = Dataset.load_from_disk(WORKDIR + "/train")
  test_ds = Dataset.load_from_disk(WORKDIR + "/test")
  ids = set(train_ds['movie_id'])
else:
  # sample ids
  ids = set()
  random.seed(1234)
  while len(ids) < 50:
    new_id = random.choice(all_ids_reviews)
    if int(new_id[2:]) in all_ids_metadata:
      ids.add(new_id)

ids_set_ints = set([int(x[2:]) for x in ids])
id_int2id = {int(x[2:]):x for x in ids}

print(len(ids))
reviews_subset = reviews_df[reviews_df['movie_id'].isin(ids)]
print(len(reviews_subset), reviews_subset.columns)

In [ ]:
movies_chosen_df = metadata_df[metadata_df['imdb_id'].isin(ids)][['imdb_id','original_title']]

In [ ]:
movies_chosen_df['amount_reviews'] = [len(reviews_subset[reviews_subset['movie_id'] == imdb_id]) for imdb_id in movies_chosen_df['imdb_id']]

In [ ]:
movies_chosen_df

###Identify secrets (cast)

In [ ]:
def process_characters(s):
  chars = s.replace(" / ","/").split("/")
  res = []
  for c in chars:
    if " (" in c:
      c = c[:c.index(" (")]
    if c not in res:
      res.append(c)
  return res

imdbid2cast = {imdbid:eval(list(credits_df[credits_df['id']==imdbid2tid[imdbid]]['cast'])[0]) for \
                    imdbid in ids_set_ints if imdbid in imdbid2tid and len(credits_df[credits_df['id']==imdbid2tid[imdbid]]) > 0}
imdbid2characters = {imdbid:process_characters(" / ".join([x['character'] for x in cast if x['character']])) for imdbid, cast in imdbid2cast.items()}

imdbid2actors = {imdbid:process_characters(" / ".join([x['name'] for x in cast if x['name']])) for imdbid, cast in imdbid2cast.items()}

ids_unique = list(imdbid2characters.keys())

In [ ]:
# Find replacements for secrets for secret inference attack

import random
import os
import pickle
from tqdm import tqdm
from sklearn.model_selection import train_test_split
old_reviews_df = reviews_df[(reviews_df['release_date'] >= '2014-06') * (reviews_df['release_date'] < '2016')]
all_ids_old_reviews = list(old_reviews_df['movie_id'])
ids_old = set()
random.seed(1234)
while len(ids_old) < 50:
  new_id = random.choice(all_ids_old_reviews)
  if int(new_id[2:]) in all_ids_metadata:
    ids_old.add(new_id)

ids_set_ints_old = set([int(x[2:]) for x in ids_old])
id_int2id_old = {int(x[2:]):x for x in ids_old}

imdbid2cast_old = {imdbid:eval(list(credits_df[credits_df['id']==imdbid2tid[imdbid]]['cast'])[0]) for \
                    imdbid in ids_set_ints_old if imdbid in imdbid2tid and len(credits_df[credits_df['id']==imdbid2tid[imdbid]]) > 0}
imdbid2characters_old = {imdbid:process_characters(" / ".join([x['character'] for x in cast if x['character']])) for imdbid, cast in imdbid2cast_old.items()}

imdbid2actors_old = {imdbid:process_characters(" / ".join([x['name'] for x in cast if x['name']])) for imdbid, cast in imdbid2cast_old.items()}

def count_name(movie_id, name):
  data = reviews_df[reviews_df['movie_id'] == movie_id]['review_text']
  return sum([x.count(name) for x in data])
count_name("tt2948356", 'Ginnifer Goodwin')

if os.path.exists(WORKDIR + "/cast_names_counts.pkl"):
  counts = pickle.load(open(WORKDIR + "/cast_names_counts.pkl", "rb"))
else:
  counts = {}
  for mid in tqdm(imdbid2actors):
    counts[mid] = {}
    for actor in imdbid2actors[mid]:
      counts[mid][actor] = count_name("tt" + str(mid), actor)

  for mid in tqdm(imdbid2actors_old):
    counts[mid] = {}
    for actor in imdbid2actors_old[mid]:
      counts[mid][actor] = count_name("tt" + str(mid), actor)
  pickle.dump(counts, open(WORKDIR + "/cast_names_counts.pkl", "wb"))

counts_non_zero = {}
for mid in counts:
  counts_non_zero[mid] = {k:v for k,v in counts[mid].items() if v > 0}

total_count = {}
for mid in imdbid2actors:
  for actor in imdbid2actors[mid]:
    total_count[actor] = total_count.get(actor, 0) + counts[mid][actor]

total_count_old = {}
for mid in imdbid2actors_old:
  for actor in imdbid2actors_old[mid]:
    total_count_old[actor] = total_count_old.get(actor, 0) + counts[mid][actor]

appears = {}
for mid in imdbid2actors:
  for actor in imdbid2actors[mid]:
    appears[actor] = appears.get(actor, 0) + 1

appears_old = {}
for mid in imdbid2actors_old:
  for actor in imdbid2actors_old[mid]:
    appears_old[actor] = appears_old.get(actor, 0) + 1

all_secrets = sorted(total_count.items(), key=lambda x:x[1], reverse=True)
all_secrets_old = sorted(total_count_old.items(), key=lambda x:x[1], reverse=True)

if os.path.exists(WORKDIR + "/actor_pairs.pkl"):
  actor_pairs = pickle.load(open(WORKDIR + "/actor_pairs.pkl", "rb"))
else:
  actor_pairs = {}
  chosen_actors = set()
  for s, c in all_secrets:
    if c == 0:
      break
    closest_actors = sorted(all_secrets_old, key=lambda x: abs(x[1]-c))
    for actor, c2 in closest_actors:
      if actor not in chosen_actors:
        chosen_actors.add(actor)
        actor_pairs[s] = (actor, abs(c - c2) / c)
        break
  pickle.dump(actor_pairs, open(WORKDIR + "/actor_pairs.pkl", "wb"))

def replace_secret_actor(text, movie_id):
  movie_id = int(movie_id[2:])
  if movie_id not in counts_non_zero:
    return text
  for secret in counts_non_zero[movie_id]:
    text = text.replace(secret, actor_pairs[secret][0])
  return text

In [ ]:
# needed for secret inference attack
reviews_subset["review_filtered"] = reviews_subset.apply(lambda x: replace_secret_actor(x["review_text"], x["movie_id"]), axis=1)

In [ ]:
from sklearn.model_selection import train_test_split
train_reviews, test_reviews = train_test_split(reviews_subset, test_size=0.1, random_state=1234, stratify=reviews_subset['movie_id'])

### Train, test and halves split

In [ ]:
import json
import os
if not os.path.exists(WORKDIR + "/train"):
  train_ds = Dataset.from_pandas(train_reviews)
  test_ds = Dataset.from_pandas(test_reviews)
  train_ds.save_to_disk(WORKDIR + "/train")
  test_ds.save_to_disk(WORKDIR + "/test")

print(len(train_ds), len(test_ds), len(train_ds) + len(test_ds))


In [ ]:
import random

if os.path.exists(WORKDIR + "/parts_2/train0"):
  train0 = Dataset.load_from_disk(WORKDIR + "/parts_2/train0")
  train1 = Dataset.load_from_disk(WORKDIR + "/parts_2/train1")
  test0 = Dataset.load_from_disk(WORKDIR + "/parts_2/test0")
  test1 = Dataset.load_from_disk(WORKDIR + "/parts_2/test1")
  ids0 = set(train0['movie_id'])
  ids1 = set(train1['movie_id'])
else:
  random.seed(1234)
  ids_list = list(ids)
  random.shuffle(ids_list)
  assert(len(ids_list) == 50)
  ids0 = set(ids_list[:25])
  ids1 = set(ids_list[25:])
  train0 = Dataset.from_list([x for x in train_ds if x['movie_id'] in ids0])
  train1 = Dataset.from_list([x for x in train_ds if x['movie_id'] in ids1])
  test0 = Dataset.from_list([x for x in test_ds if x['movie_id'] in ids0])
  test1 = Dataset.from_list([x for x in test_ds if x['movie_id'] in ids1])
  train0.save_to_disk(WORKDIR + "/parts_2/train0")
  train1.save_to_disk(WORKDIR + "/parts_2/train1")
  test0.save_to_disk(WORKDIR + "/parts_2/test0")
  test1.save_to_disk(WORKDIR + "/parts_2/test1")

In [ ]:
reviews_subset_old = reviews_df[reviews_df['movie_id'].isin(ids_old)]
train_reviews_old, test_reviews_old = train_test_split(reviews_subset_old, test_size=len(test_reviews), random_state=1234, stratify=reviews_subset_old['movie_id'])
test_reviews_old['movie_id'] = list(test_reviews['movie_id'])
if not os.path.exists(WORKDIR + "/eval_others"):
  eval_ds = Dataset.from_pandas(test_reviews_old)
  eval_ds.save_to_disk(WORKDIR + "/eval_others")
else:
  eval_ds = Dataset.load_from_disk(WORKDIR + "/eval_others")

if not os.path.exists(WORKDIR + "/tbs_others"):
  tbs_ds = Dataset.from_pandas(train_reviews_old)
  tbs_ds.save_to_disk(WORKDIR + "/tbs_others")
else:
  tbs_ds = Dataset.load_from_disk(WORKDIR + "/tbs_others")

## Training

### FT ALL

In [ ]:
for num_epochs in [1,2,4]:
  ac = acm.ACModel(
      workdir=f"/content/epochs_{num_epochs}/one_model",
      final_model_path = WORKDIR + f"/epochs_{num_epochs}/one_model",
      train_ds=train_ds,
      test_ds=eval_ds,
      text_column="review_text",
      context_column="movie_id",
      mode='reg',
      r=64)
  ac.run(num_train_epochs=num_epochs, eval_base=False)

peft model exists, loading from /content/drive/MyDrive/thesis/movies_run_24_7_5/epochs_1/one_model


/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1119: UserWarning: fan_in_fan_out is set to False but the target module is `Conv1D`. Setting fan_in_fan_out to True.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1110: UserWarning: fan_in_fan_out is set to True but the target module is `torch.nn.Linear`. Setting fan_in_fan_out to False.
  warnings.warn(
100%|██████████| 316/316 [00:47<00:00,  6.68it/s]



peft model loss: 3.916457945787454. ppl: 50.22223946308428
peft model exists, loading from /content/drive/MyDrive/thesis/movies_run_24_7_5/epochs_2/one_model


100%|██████████| 316/316 [00:47<00:00,  6.71it/s]



peft model loss: 3.8772623486156705. ppl: 48.29182774977111
peft model exists, loading from /content/drive/MyDrive/thesis/movies_run_24_7_5/epochs_4/one_model


100%|██████████| 316/316 [00:47<00:00,  6.69it/s]


peft model loss: 3.840263199202622. ppl: 46.537721519203444


In [ ]:
ac.load_base_model()
print(ac.eval_model('base'))

100%|██████████| 316/316 [00:42<00:00,  7.44it/s]

(4.220704163931593, 316)


In [ ]:
for num_epochs in [1,2,4]:
  ac_bs = acm.ACModel(
      workdir=f"/content/epochs_{num_epochs}/bs_model",
      final_model_path = WORKDIR + f"/epochs_{num_epochs}/bs_model",
      train_ds=tbs_ds,
      test_ds=test_ds,
      text_column="review_text",
      context_column="movie_id",
      mode='reg',
      r=64)
  ac_bs.run(num_train_epochs=num_epochs, eval_base=False)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1119: UserWarning: fan_in_fan_out is set to False but the target module is `Conv1D`. Setting fan_in_fan_out to True.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1110: UserWarning: fan_in_fan_out is set to True but the target module is `torch.nn.Linear`. Setting fan_in_fan_out to False.
  warnings.warn(


using reg_formatting_func for formatting


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_deprecation.py:100: FutureWarning: Deprecated argument(s) used in '__init__': max_seq_length. Will not be supported from version '1.0.0'.

Deprecated positional argument(s) used in SFTTrainer, please use the SFTConfig to set these arguments instead.
  warnings.warn(message, FutureWarning)
/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1965: FutureWarning: `--push_to_hub_token` is deprecated and will be removed in version 5 of 🤗 Transformers. Use `--hub_token` instead.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/trl/trainer/sft_trainer.py:269: UserWarning: You passed a `max_seq_length` argument to the SFTTrainer, the value you passed will override the one in the `SFTConfig`.
  warnings.warn(


Map:   0%|          | 0/25474 [00:00<?, ? examples/s]

Map:   0%|          | 0/2527 [00:00<?, ? examples/s]

...

Map:   0%|          | 0/2527 [00:00<?, ? examples/s]

/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers fou

train time: 39.71706519921621 minutes
saving peft model to /content/drive/MyDrive/thesis/movies_run_24_7_5/epochs_4/bs_model


100%|██████████| 316/316 [00:42<00:00,  7.44it/s]


peft model loss: 3.8032470873639554. ppl: 44.84656905507017


### FT HALF

In [ ]:
for num_epochs in [1,2,4]:
  ac_half0 = acm.ACModel(
      workdir=f"/content/epochs_{num_epochs}/half0",
      final_model_path = WORKDIR + f"/epochs_{num_epochs}/half0",
      train_ds=train0,
      test_ds=test0,
      text_column="review_text",
      context_column="movie_id",
      mode='reg',
      r=64)
  ac_half0.run(num_train_epochs=num_epochs, eval_base=False)
  ac_half0.merge_and_save_model()

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/656 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/479M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/74.0 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/25.0 [00:00<?, ?B/s]

...


peft model loss: 3.8208853163809144. ppl: 45.64460035073846
saving merged model to /content/drive/MyDrive/thesis/movies_run_24_7_5/epochs_1/half0_full
peft model exists, loading from /content/drive/MyDrive/thesis/movies_run_24_7_5/epochs_2/half0


/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1119: UserWarning: fan_in_fan_out is set to False but the target module is `Conv1D`. Setting fan_in_fan_out to True.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1110: UserWarning: fan_in_fan_out is set to True but the target module is `torch.nn.Linear`. Setting fan_in_fan_out to False.
  warnings.warn(
100%|██████████| 159/159 [00:22<00:00,  6.95it/s]



peft model loss: 3.728355592151858. ppl: 41.610627032347516
saving merged model to /content/drive/MyDrive/thesis/movies_run_24_7_5/epochs_2/half0_full
peft model exists, loading from /content/drive/MyDrive/thesis/movies_run_24_7_5/epochs_4/half0


/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1119: UserWarning: fan_in_fan_out is set to False but the target module is `Conv1D`. Setting fan_in_fan_out to True.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1110: UserWarning: fan_in_fan_out is set to True but the target module is `torch.nn.Linear`. Setting fan_in_fan_out to False.
  warnings.warn(
100%|██████████| 159/159 [00:22<00:00,  6.95it/s]



peft model loss: 3.6304776983441047. ppl: 37.730836270868
saving merged model to /content/drive/MyDrive/thesis/movies_run_24_7_5/epochs_4/half0_full


In [ ]:
for num_epochs in [1,2,4]:
  ac_half1 = acm.ACModel(
      workdir=f"/content/epochs_{num_epochs}/half1",
      final_model_path = WORKDIR + f"/epochs_{num_epochs}/half1",
      train_ds=train1,
      test_ds=test1,
      text_column="review_text",
      context_column="movie_id",
      mode='reg',
      r=64)
  ac_half1.run(num_train_epochs=num_epochs, eval_base=False)
  ac_half1.merge_and_save_model()

/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1119: UserWarning: fan_in_fan_out is set to False but the target module is `Conv1D`. Setting fan_in_fan_out to True.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1110: UserWarning: fan_in_fan_out is set to True but the target module is `torch.nn.Linear`. Setting fan_in_fan_out to False.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_deprecation.py:100: FutureWarning: Deprecated argument(s) used in '__init__': max_seq_length. Will not be supported from version '1.0.0'.

Deprecated positional argument(s) used in SFTTrainer, please use the SFTConfig to set these arguments instead.
  warnings.warn(message, FutureWarning)


using reg_formatting_func for formatting


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1965: FutureWarning: `--push_to_hub_token` is deprecated and will be removed in version 5 of 🤗 Transformers. Use `--hub_token` instead.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/trl/trainer/sft_trainer.py:269: UserWarning: You passed a `max_seq_length` argument to the SFTTrainer, the value you passed will override the one in the `SFTConfig`.
  warnings.warn(


Map:   0%|          | 0/11333 [00:00<?, ? examples/s]

Map:   0%|          | 0/1259 [00:00<?, ? examples/s]

...

Map:   0%|          | 0/1259 [00:00<?, ? examples/s]

/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers fou

train time: 15.293026077747346 minutes
saving peft model to /content/drive/MyDrive/thesis/movies_run_24_7_5/epochs_4/half1


100%|██████████| 158/158 [00:21<00:00,  7.43it/s]



peft model loss: 3.6757550873333895. ppl: 39.4784552871053
saving merged model to /content/drive/MyDrive/thesis/movies_run_24_7_5/epochs_4/half1_full


### PER AL

In [ ]:
reload(acm)
import os

random.seed(1234)
eval_shuf = [x for x in eval_ds]
random.shuffle(eval_shuf)

reses = []
for num_epochs in [1,2,4]:
  main_dir = f"/content/epochs_{num_epochs}/by_id"
  if not os.path.exists(main_dir):
    os.makedirs(main_dir)
  res = []
  train_time = 0
  ds_ind = 0
  for i, movie_id in enumerate(ids):
    next_ds_ind = ds_ind + len(eval_shuf) / len(ids)
    print(f"{i}/{len(ids)}")
    train_ds_movie = Dataset.from_list([x for x in train_ds if movie_id == x['movie_id']])
    test_ds_movie = Dataset.from_list(eval_shuf[int(round(ds_ind)):int(round(next_ds_ind))])
    ds_ind = next_ds_ind
    ac3 = acm.ACModel(
      workdir=os.path.join(main_dir, movie_id),
      final_model_path = WORKDIR + f"/epochs_{num_epochs}/by_id/{movie_id}",
      train_ds=train_ds_movie,
      test_ds=test_ds_movie,
      text_column="review_text",
      context_column="movie_id",
      mode='reg',
      r=64)
    test_loss = ac3.run(eval_base=False, num_train_epochs=num_epochs)
    train_time += ac3.train_time
    res.append((movie_id, len(train_ds_movie), len(test_ds_movie), test_loss))
  print(f"{train_time=}")
  reses.append(res)

0/50


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/656 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/479M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/74.0 [00:00<?, ?B/s]

...

Map:   0%|          | 0/51 [00:00<?, ? examples/s]

/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")


train time: 0.9000049551328023 minutes
saving peft model to /content/drive/MyDrive/thesis/movies_run_24_7_5/epochs_4/by_id/tt3385516


100%|██████████| 7/7 [00:00<00:00,  7.31it/s]


peft model loss: 4.142486912863595. ppl: 62.95920096425041
train_time=27.8680800040563


### FT DOMBA PER AL

In [ ]:
reload(acm)
import os
from peft import PeftModel

ft_reses = []
for num_epochs in [1,2,4]:
  main_dir = f"/content/epochs_{num_epochs}/by_id_half"
  if not os.path.exists(main_dir):
    os.makedirs(main_dir)
  ft_res = []
  train_time = 0

  for i, movie_id in enumerate(ids):
    print(f"{i}/{len(ids)}")
    train_ds_movie = Dataset.from_list([x for x in train_ds if movie_id == x['movie_id']])
    test_ds_movie = Dataset.from_list([x for x in test_ds if movie_id == x['movie_id']])
    half = 1 if movie_id in ids0 else 0

    ac4 = acm.ACModel(
      workdir=os.path.join(main_dir,str(half),movie_id),
      final_model_path = WORKDIR + f"/epochs_{num_epochs}/by_id_half{half}/{movie_id}",
      train_ds=train_ds_movie,
      test_ds=test_ds_movie,
      text_column="review_text",
      context_column="movie_id",
      mode='reg',
      r=64,
      base_model_path = WORKDIR + f"/epochs_{num_epochs}/half{half}_full")

    test_loss = ac4.run(eval_base=False, num_train_epochs=num_epochs)
    train_time += ac4.train_time
    ft_res.append((movie_id, half, len(train_ds_movie), len(test_ds_movie), test_loss))
  print(f"{train_time=}")
  ft_reses.append(ft_res)

0/50


/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1119: UserWarning: fan_in_fan_out is set to False but the target module is `Conv1D`. Setting fan_in_fan_out to True.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1110: UserWarning: fan_in_fan_out is set to True but the target module is `torch.nn.Linear`. Setting fan_in_fan_out to False.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_deprecation.py:100: FutureWarning: Deprecated argument(s) used in '__init__': max_seq_length. Will not be supported from version '1.0.0'.

Deprecated positional argument(s) used in SFTTrainer, please use the SFTConfig to set these arguments instead.
  warnings.warn(message, FutureWarning)


using reg_formatting_func for formatting


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1965: FutureWarning: `--push_to_hub_token` is deprecated and will be removed in version 5 of 🤗 Transformers. Use `--hub_token` instead.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/trl/trainer/sft_trainer.py:269: UserWarning: You passed a `max_seq_length` argument to the SFTTrainer, the value you passed will override the one in the `SFTConfig`.
  warnings.warn(


Map:   0%|          | 0/284 [00:00<?, ? examples/s]

...

Map:   0%|          | 0/71 [00:00<?, ? examples/s]

/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")


train time: 0.907160758972168 minutes
saving peft model to /content/drive/MyDrive/thesis/movies_run_24_7_5/epochs_4/by_id_half0/tt3385516


100%|██████████| 9/9 [00:01<00:00,  6.69it/s]


peft model loss: 3.4873449272579617. ppl: 32.69901408876346
train_time=28.538033191363024


## Evaluation

###Canaries

####setup

In [ ]:
all_words = set()
for text in reviews_df['review_text']:
  all_words.update(set(text.split()))
all_words = [w for w in all_words if w.isalpha()]

In [ ]:
import random
print(len(all_words), random.sample(all_words, 10))

275579 ['Prosecuted', 'Dostoyevskian', 'Scamander', 'Housing', 'Lionell', 'Tenkû', 'Neborski', 'Dustoff', 'Dicaprios', 'Delgado']


In [ ]:
ids_unique = [id_int2id[movie_id] for movie_id in imdbid2actors.keys()]
movie2secret = {movie_id:imdbid2actors[int(movie_id[2:])] for movie_id in ids_unique}
ev = eac.Evaluator(ids_unique, 'movie_id', movie2secret, {a:b[0] for a,b in actor_pairs.items()},
             "review_text", "review_filtered", train_ds[0].keys(), WORKDIR + "/EVALS")

In [ ]:
if os.path.exists(WORKDIR + "/canaries"):
  print("loading canaries")
  canaries = pickle.load(open(WORKDIR + "/canaries","rb"))
  can_train_ds = Dataset.load_from_disk(WORKDIR + "/can_train_ds")
else:
  canaries, can_train_ds = ev.get_canaries_ds(train_ds, all_words)
  pickle.dump(canaries, open(WORKDIR + "/canaries","wb"))
  can_train_ds.save_to_disk(WORKDIR + "/can_train_ds")
can_train0 = Dataset.from_list([x for x in can_train_ds if x['movie_id'] in ids0])
can_train1 = Dataset.from_list([x for x in can_train_ds if x['movie_id'] in ids1])

Saving the dataset (0/1 shards):   0%|          | 0/29654 [00:00<?, ? examples/s]

####train

In [ ]:
for num_epochs in [1,2,4]:
  can_ac = acm.ACModel(
      workdir=f"/content/epochs_{num_epochs}/can_one_model",
      final_model_path = WORKDIR + f"/epochs_{num_epochs}/can_one_model",
      train_ds=can_train_ds,
      test_ds=eval_ds,
      text_column="review_text",
      context_column="movie_id",
      mode='reg',
      r=64)
  can_ac.run(num_train_epochs=num_epochs, eval_base=False)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/656 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/479M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/74.0 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/25.0 [00:00<?, ?B/s]

...

Map:   0%|          | 0/2527 [00:00<?, ? examples/s]

/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers fou

train time: 46.946894601980844 minutes
saving peft model to /content/drive/MyDrive/thesis/movies_run_24_7_5/epochs_4/can_one_model


100%|██████████| 316/316 [00:44<00:00,  7.12it/s]


peft model loss: 3.8292637889898278. ppl: 46.028638966448185


In [ ]:
for num_epochs in [1,2,4]:
  can_ac_half0 = acm.ACModel(
      workdir=f"/content/epochs_{num_epochs}/can_half0",
      final_model_path = WORKDIR + f"/epochs_{num_epochs}/can_half0",
      train_ds=can_train0,
      test_ds=eval_ds,
      text_column="review_text",
      context_column="movie_id",
      mode='reg',
      r=64)
  can_ac_half0.run(num_train_epochs=num_epochs, eval_base=False)

  can_ac_half1 = acm.ACModel(
      workdir=f"/content/epochs_{num_epochs}/can_half1",
      final_model_path = WORKDIR + f"/epochs_{num_epochs}/can_half1",
      train_ds=can_train1,
      test_ds=eval_ds,
      text_column="review_text",
      context_column="movie_id",
      mode='reg',
      r=64)
  can_ac_half1.run(num_train_epochs=num_epochs, eval_base=False)

/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1119: UserWarning: fan_in_fan_out is set to False but the target module is `Conv1D`. Setting fan_in_fan_out to True.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1110: UserWarning: fan_in_fan_out is set to True but the target module is `torch.nn.Linear`. Setting fan_in_fan_out to False.
  warnings.warn(


using reg_formatting_func for formatting


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_deprecation.py:100: FutureWarning: Deprecated argument(s) used in '__init__': max_seq_length. Will not be supported from version '1.0.0'.

Deprecated positional argument(s) used in SFTTrainer, please use the SFTConfig to set these arguments instead.
  warnings.warn(message, FutureWarning)
/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1965: FutureWarning: `--push_to_hub_token` is deprecated and will be removed in version 5 of 🤗 Transformers. Use `--hub_token` instead.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/trl/trainer/sft_trainer.py:269: UserWarning: You passed a `max_seq_length` argument to the SFTTrainer, the value you passed will override the one in the `SFTConfig`.
  warnings.warn(


Map:   0%|          | 0/14865 [00:00<?, ? examples/s]

Map:   0%|          | 0/2527 [00:00<?, ? examples/s]

...

Map:   0%|          | 0/2527 [00:00<?, ? examples/s]

/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.
  warnings.warn("Setting `save_embedding_layers` to `True` as embedding layers found in `target_modules`.")
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:180: UserWarning: Setting `save_embedding_layers` to `True` as embedding layers fou

train time: 22.926572597026826 minutes
saving peft model to /content/drive/MyDrive/thesis/movies_run_24_7_5/epochs_4/can_half1


100%|██████████| 316/316 [00:44<00:00,  7.08it/s]


peft model loss: 3.9582888506635836. ppl: 52.36764038519117


####eval

In [ ]:
ids_unique = [id_int2id[movie_id] for movie_id in imdbid2actors.keys()]
movie2secret = {movie_id:imdbid2actors[int(movie_id[2:])] for movie_id in ids_unique}
ev = eac.Evaluator(ids_unique, 'movie_id', movie2secret, {a:b[0] for a,b in actor_pairs.items()},
             "review_text", "review_filtered", train_ds[0].keys(), WORKDIR + "/EVALS")

In [ ]:
all_cans, can_eval_ds = ev.add_false_canaries(canaries, all_words, 100)

In [ ]:
for csv_name in ["canary_attack"]:
  path = WORKDIR + f"/EVALS/{csv_name}.csv"
  if os.  path.exists(path):
    os.remove(path)

for num_epochs in [1,2,4]:
  ac = acm.ACModel(
      workdir=f"/content/epochs_{num_epochs}/one_model",
      final_model_path = WORKDIR + f"/epochs_{num_epochs}/one_model",
      train_ds=train_ds,
      test_ds=test_ds,
      text_column="review_text",
      context_column="movie_id",
      mode='reg',
      r=64)

  can_ac = acm.ACModel(
      workdir=f"/content/epochs_{num_epochs}/can_one_model",
      final_model_path = WORKDIR + f"/epochs_{num_epochs}/can_one_model",
      train_ds=can_train_ds,
      test_ds=test_ds,
      text_column="review_text",
      context_column="movie_id",
      mode='reg',
      r=64)

  can_ac_half0 = acm.ACModel(
      workdir=f"/content/epochs_{num_epochs}/can_half0",
      final_model_path = WORKDIR + f"/epochs_{num_epochs}/can_half0",
      train_ds=can_train0,
      test_ds=eval_ds,
      text_column="review_text",
      context_column="movie_id",
      mode='reg',
      r=64)

  can_ac_half1 = acm.ACModel(
      workdir=f"/content/epochs_{num_epochs}/can_half1",
      final_model_path = WORKDIR + f"/epochs_{num_epochs}/can_half1",
      train_ds=can_train1,
      test_ds=eval_ds,
      text_column="review_text",
      context_column="movie_id",
      mode='reg',
      r=64)

  ev.canary_attack(ac, ac, [min_avg], all_cans, can_eval_ds, 100, f"e{num_epochs}_baseline_100", f"e{num_epochs}_baseline", "canary_attack", field_pref="can_")
  ev.canary_attack(can_ac, can_ac, [min_avg], all_cans, can_eval_ds, 100, f"e{num_epochs}_ft_all_100", f"e{num_epochs}_ft_all", "canary_attack", field_pref="can_")
  avg_funcs = [arithmetic_avg, geometric_avg, submix_3e1, submix_1e2, min_avg, harmonic_avg]
  ev.canary_attack(can_ac_half0, can_ac_half1, avg_funcs, all_cans, can_eval_ds, 100, f"e{num_epochs}_avgs_100", f"e{num_epochs}", "canary_attack", field_pref="can_")

neg_per_pos=100


/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1119: UserWarning: fan_in_fan_out is set to False but the target module is `Conv1D`. Setting fan_in_fan_out to True.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1110: UserWarning: fan_in_fan_out is set to True but the target module is `torch.nn.Linear`. Setting fan_in_fan_out to False.
  warnings.warn(
100%|██████████| 3030/3030 [02:56<00:00, 17.18it/s]


neg_per_pos=100


100%|██████████| 3030/3030 [02:51<00:00, 17.63it/s]


neg_per_pos=100


...

neg_per_pos=100


/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1119: UserWarning: fan_in_fan_out is set to False but the target module is `Conv1D`. Setting fan_in_fan_out to True.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1110: UserWarning: fan_in_fan_out is set to True but the target module is `torch.nn.Linear`. Setting fan_in_fan_out to False.
  warnings.warn(
100%|██████████| 3030/3030 [02:52<00:00, 17.55it/s]


neg_per_pos=100


/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1119: UserWarning: fan_in_fan_out is set to False but the target module is `Conv1D`. Setting fan_in_fan_out to True.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1110: UserWarning: fan_in_fan_out is set to True but the target module is `torch.nn.Linear`. Setting fan_in_fan_out to False.
  warnings.warn(
100%|██████████| 3030/3030 [05:52<00:00,  8.60it/s]


--------arithmetic_avg--------
--------geometric_avg--------
--------submix_3e1--------
--------submix_1e2--------
--------min_avg--------
--------harmonic_avg--------


### All but canaries

In [88]:
ids_unique = [id_int2id[movie_id] for movie_id in imdbid2actors.keys()]
movie2secret = {movie_id:imdbid2actors[int(movie_id[2:])] for movie_id in ids_unique}
ev = eac.Evaluator(ids_unique, 'movie_id', movie2secret, {a:b[0] for a,b in actor_pairs.items()},
             "review_text", "review_filtered", train_ds[0].keys(), WORKDIR + "/EVALS")

In [ ]:
for num_epochs in [1,2,4]:
  print("NUM EPOCHS:", num_epochs)
  ac = acm.ACModel(
            workdir=f"/content/epochs_{num_epochs}/one_model",
            final_model_path = WORKDIR + f"/epochs_{num_epochs}/one_model",
            train_ds=train_ds,
            test_ds=test_ds,
            text_column="review_text",
            context_column="movie_id",
            mode='reg',
            r=64)
  ac.load_base_model()
  base_model = ac.base_model
  ac_half0 = acm.ACModel(
            workdir=f"/content/epochs_{num_epochs}/half0",
            final_model_path = WORKDIR + f"/epochs_{num_epochs}/half0",
            train_ds=train0,
            test_ds=test0,
            text_column="review_text",
            context_column="movie_id",
            mode='reg',
            r=64)
  ac_half0.load_base_model()
  ac_half0.load_peft_model()
  ac_half0.load_base_model()

  ac_half1 = acm.ACModel(
            workdir=f"/content/epochs_{num_epochs}/half1",
            final_model_path = WORKDIR + f"/epochs_{num_epochs}/half1",
            train_ds=train1,
            test_ds=test1,
            text_column="review_text",
            context_column="movie_id",
            mode='reg',
            r=64)
  ac_half1.load_base_model()
  ac_half1.load_peft_model()
  ac_half1.load_base_model()

  avg_funcs = [arithmetic_avg,geometric_avg, submix_3e1, submix_1e2, min_avg, harmonic_avg]

  ev.eval(ac, ac, [no_avg], test_ds, f"e{num_epochs}_auth_ft_all", only_secrets=False)
  ev.eval(ac, ac, [no_avg], eval_ds, f"e{num_epochs}_held_out_ft_all", only_secrets=False)
  ev.eval(ac, ac, [no_avg], test_ds, f"e{num_epochs}_secrets_ft_all")
  ev.eval(ac, ac, [no_avg], test_ds, f"e{num_epochs}_secrets_ft_all", fil=True)

  ev.eval(ac_half0, ac_half0, [no_avg], test1, f"e{num_epochs}_auth_half0", only_secrets=False)
  ev.eval(ac_half0, ac_half0, [no_avg], eval_ds, f"e{num_epochs}_held_out_half0", only_secrets=False)
  ev.eval(ac_half0, ac_half0, [no_avg], test1, f"e{num_epochs}_secrets_half0")
  ev.eval(ac_half0, ac_half0, [no_avg], test1, f"e{num_epochs}_secrets_half0", fil=True)

  ev.eval(ac_half1, ac_half1, [no_avg], test0, f"e{num_epochs}_auth_half1", only_secrets=False)
  ev.eval(ac_half1, ac_half1, [no_avg], eval_ds, f"e{num_epochs}_held_out_half1", only_secrets=False)
  ev.eval(ac_half1, ac_half1, [no_avg], test0, f"e{num_epochs}_secrets_half1")
  ev.eval(ac_half1, ac_half1, [no_avg], test0, f"e{num_epochs}_secrets_half1", fil=True)

  ev.eval(ac_half0, ac_half1, avg_funcs, test_ds, f"e{num_epochs}_auth", only_secrets=False)
  ev.eval(ac_half0, ac_half1, avg_funcs, eval_ds, f"e{num_epochs}_held_out", only_secrets=False)
  ev.eval(ac_half0, ac_half1, avg_funcs, test_ds, f"e{num_epochs}_secrets")
  ev.eval(ac_half0, ac_half1, avg_funcs, test_ds, f"e{num_epochs}_secrets", fil=True)



NUM EPOCHS: 1


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/656 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/479M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/74.0 [00:00<?, ?B/s]

...

100%|██████████| 4/4 [00:05<00:00,  1.32s/it]


46/48


100%|██████████| 10/10 [00:12<00:00,  1.23s/it]


47/48


100%|██████████| 4/4 [00:05<00:00,  1.29s/it]


In [ ]:
del ac

In [89]:
for num_epochs in [1,2,4]:
  print("NUM EPOCHS:", num_epochs)

  ac_half0 = acm.ACModel(
            workdir=f"/content/epochs_{num_epochs}/half0",
            final_model_path = WORKDIR + f"/epochs_{num_epochs}/half0",
            train_ds=train0,
            test_ds=test0,
            text_column="review_text",
            context_column="movie_id",
            mode='reg',
            r=64)
  ac_half0.load_base_model()
  ac_half0.load_peft_model()
  ac_half0.load_base_model()

  ac_half1 = acm.ACModel(
            workdir=f"/content/epochs_{num_epochs}/half1",
            final_model_path = WORKDIR + f"/epochs_{num_epochs}/half1",
            train_ds=train1,
            test_ds=test1,
            text_column="review_text",
            context_column="movie_id",
            mode='reg',
            r=64)
  ac_half1.load_base_model()
  ac_half1.load_peft_model()
  ac_half1.load_base_model()

  main_dir_half = f"/content/epochs_{num_epochs}/by_id_half"
  ac_pal_agg0 = {}
  ac_pal_agg1 = {}
  ac_pal_agg0_ne = {}
  ac_pal_agg1_ne = {}
  for i, movie_id in enumerate(ids_unique):
    prev_id = ids_unique[(i-1)%len(ids_unique)]
    if movie_id in ids0:
      ac_0 = ac_half0
      ac_1 = acm.ACModel(
        workdir=os.path.join(main_dir_half,"1",movie_id),
        final_model_path=WORKDIR + f"/epochs_{num_epochs}/by_id_half1/{movie_id}",
        train_ds=train_ds,
        test_ds=test_ds,
        text_column="review_text",
        context_column="movie_id",
        mode='reg',
        r=64,
        base_model_path = WORKDIR + f"/epochs_{num_epochs}/half1_full")
      ac_1.load_base_model()
      ac_1.load_peft_model()
    else:
      ac_1 = ac_half1
      ac_0 = acm.ACModel(
        workdir=os.path.join(main_dir_half,"0",movie_id),
        final_model_path=WORKDIR + f"/epochs_{num_epochs}/by_id_half0/{movie_id}",
        train_ds=train_ds,
        test_ds=test_ds,
        text_column="review_text",
        context_column="movie_id",
        mode='reg',
        r=64,
        base_model_path = WORKDIR + f"/epochs_{num_epochs}/half0_full")
      ac_0.load_base_model()
      ac_0.load_peft_model()

    ac_pal_agg0[movie_id] = ac_0
    ac_pal_agg0_ne[prev_id] = ac_0
    ac_pal_agg1[movie_id] = ac_1
    ac_pal_agg1_ne[prev_id] = ac_1

  ev.eval(ac_pal_agg0, ac_pal_agg1, avg_funcs, test_ds, f"e{num_epochs}_auth_pal", only_secrets=False, ref_model=base_model, load_models=False)
  ev.eval(ac_pal_agg0, ac_pal_agg1, avg_funcs, eval_ds, f"e{num_epochs}_held_out_pal", only_secrets=False, ref_model=base_model, load_models=False)
  ev.eval(ac_pal_agg0, ac_pal_agg1, avg_funcs, test_ds, f"e{num_epochs}_secrets_pal", ref_model=base_model, next_al=True, load_models=False)
  ev.eval(ac_pal_agg0, ac_pal_agg1, avg_funcs, test_ds, f"e{num_epochs}_secrets_pal", fil=True, ref_model=base_model, next_al=True, load_models=False)
  ev.eval(ac_pal_agg0, ac_pal_agg1, avg_funcs, test_ds, f"e{num_epochs}_exp_pal", ref_model=base_model, next_al=True, load_models=False, only_secrets=False, overide=True)

NUM EPOCHS: 1


/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1119: UserWarning: fan_in_fan_out is set to False but the target module is `Conv1D`. Setting fan_in_fan_out to True.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/layer.py:1110: UserWarning: fan_in_fan_out is set to True but the target module is `torch.nn.Linear`. Setting fan_in_fan_out to False.
  warnings.warn(


OutOfMemoryError: CUDA out of memory. Tried to allocate 20.00 MiB. GPU 

In [ ]:
del ac_pal_agg0, ac_pal_agg1, ac_pal_agg0_ne, ac_pal_agg1_ne, ac_half0, ac_half1

In [ ]:
ac = acm.ACModel(
            workdir=f"/content/epochs_1/one_model",
            final_model_path = WORKDIR + f"/epochs_1/one_model",
            train_ds=train_ds,
            test_ds=test_ds,
            text_column="review_text",
            context_column="movie_id",
            mode='reg',
            r=64)
ac.load_base_model()
base_model = ac.base_model

for num_epochs in [1,2,4]:
  main_dir = f"/content/epochs_{num_epochs}/by_id"
  ac_pal = {mid:acm.ACModel(
      workdir=os.path.join(main_dir, mid),
      final_model_path = WORKDIR + f"/epochs_{num_epochs}/by_id/{mid}",
      train_ds=train_ds,
      test_ds=test_ds,
      text_column="review_text",
      context_column="movie_id",
      mode='reg',
      r=64) for mid in ids_unique}
  for key in ac_pal:
    ac_pal[key].load_base_model()
    ac_pal[key].load_peft_model()
  ev.eval(ac_pal, ac_pal, [no_avg], test_ds, f"e{num_epochs}_auth_per_al", only_secrets=False, load_models=False, ref_model=base_model)
  ev.eval(ac_pal, ac_pal, [no_avg], eval_ds, f"e{num_epochs}_held_out_per_al", only_secrets=False, load_models=False, ref_model=base_model)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/656 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/479M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/74.0 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/25.0 [00:00<?, ?B/s]

...

100%|██████████| 4/4 [00:01<00:00,  2.75it/s]


46/48


100%|██████████| 10/10 [00:03<00:00,  3.08it/s]


47/48


100%|██████████| 4/4 [00:01<00:00,  2.96it/s]


In [ ]:
for csv_name in ["auth_utility", "held_out_utility", "secrets_ppl", "exposure", "sia"]:
  path = WORKDIR + f"/EVALS/{csv_name}.csv"
  if os.  path.exists(path):
    os.remove(path)


for num_epochs in [1,2,4]:
  print("NUM EPOCHS:", num_epochs)

  avgs = ["arithmetic_avg", "geometric_avg", "submix_3e1", "submix_1e2", "min_avg", "harmonic_avg"]
  avgs_pal = [f"pal_{avg}" for avg in avgs]
  names = ["ft_all", "half0", "half1"] + avgs + avgs_pal
  names2 = ['per_al'] + names

  print(f"#####AUTH-UTILITY-{num_epochs}####")
  for name in names2:
    AU_df = ev.ppl(f"e{num_epochs}_auth_{name}", f"e{num_epochs}_{name}", "auth_utility", field_pref='AU')

  print(f"#####HO-UTILITY-{num_epochs}####")
  for name in names2:
    HOU_df = ev.ppl(f"e{num_epochs}_held_out_{name}", f"e{num_epochs}_{name}", "held_out_utility", field_pref='HO')

  print(f"#####SPPL-{num_epochs}####")
  for name in names:
    SPLL_df = ev.ppl(f"e{num_epochs}_secrets_{name}", f"e{num_epochs}_{name}", "secrets_ppl", field_pref='S')

  print(f"#####EXPOSURE-{num_epochs}####")
  for name in names:
    if name.startswith("pal"):
      EXP_df = ev.exposure_eval(f"e{num_epochs}_exp_{name}", f"e{num_epochs}_{name}", "exposure")
    else:
      EXP_df = ev.exposure_eval(f"e{num_epochs}_auth_{name}", f"e{num_epochs}_{name}", "exposure")

  print(f"#####SIA-{num_epochs}####")
  for name in names:
    SIA_df = ev.sia(f"e{num_epochs}_secrets_{name}", f"e{num_epochs}_{name}", "sia")

In [ ]:
AU_df = pd.read_csv(WORKDIR + f"/EVALS/auth_utility.csv").set_index("experiment")
HOU_df = pd.read_csv(WORKDIR + f"/EVALS/held_out_utility.csv").set_index("experiment")
SPLL_df = pd.read_csv(WORKDIR + f"/EVALS/secrets_ppl.csv").set_index("experiment")
EXP_df = pd.read_csv(WORKDIR + f"/EVALS/exposure.csv").set_index("experiment")
SIA_df = pd.read_csv(WORKDIR + f"/EVALS/sia.csv").set_index("experiment")
CAN_df = pd.read_csv(WORKDIR + f"/EVALS/canary_attack.csv").set_index("experiment")

In [ ]:
all_df = AU_df.join(HOU_df, how='outer').join(SPLL_df, how='outer').join(EXP_df, how='outer').join(SIA_df, how='outer').join(CAN_df, how='outer')

In [ ]:
all_df.to_csv(WORKDIR + f"/EVALS/all_res.csv")

In [ ]:
all_df

In [ ]:
main_cols = ['HOPPL', 'AUPPL', 'SPPL', 'exp_99_true', 'sia_roc_auc', 'can_attack_score_30']
order = ['ft', 'baseline', 'half0', 'half1', 'arithmetic', 'geometric', 'submix', 'harmonic', 'min', 'per', 'pal']
def sfunc(x):
  s = x.split('_')
  res = [s[0], order.index(s[1])]
  if len(s) > 2:
    res.append(order.index(s[2]) if s[2] in order else 0)
  return res
sorted_indices = sorted(list(all_df.index), key=sfunc)
sorted_df = all_df[main_cols].sort_index(key=lambda x: [sorted_indices.index(y) for y in x]).round(2)
sorted_df.to_csv(WORKDIR + f"/EVALS/main_res.csv")
sorted_df

In [ ]:
main_cols = ['HOPPL', 'AUPPL', 'SPPL', 'exp_99_true', 'sia_roc_auc', 'can_attack_score_30']
order = ['ft', 'baseline', 'half0', 'half1', 'arithmetic', 'geometric', 'submix', 'harmonic', 'min', 'per', 'pal']
def sfunc(x):
  s = x.split('_')
  res = [s[0], order.index(s[1])]
  if len(s) > 2:
    res.append(order.index(s[2]) if s[2] in order else 0)
  return res
sorted_indices = sorted(list(all_df.index), key=sfunc)
sorted_df = all_df[main_cols].sort_index(key=lambda x: [sorted_indices.index(y) for y in x]).round(2)
sorted_df.to_csv(WORKDIR + f"/EVALS/main_res.csv")
sorted_df

HOPPL  AUPPL     SPPL   exp_99_true  sia_roc_auc  \
experiment                                                                
e1_ft_all              50.34  45.36   127.93  1.000000e+00         0.80   
e1_baseline              NaN    NaN      NaN           NaN          NaN   
e1_half0               53.98  55.85  2353.42  1.000000e+00         0.45   
e1_half1               53.71  53.44  1787.28  1.000000e+00         0.48   
e1_arithmetic_avg      52.03  47.83   186.89  1.029106e+05         0.79   
e1_geometric_avg       52.20  49.08   379.18  2.544300e+02         0.76   
e1_submix_1e2          60.32  61.08  1425.96  4.790000e+01         0.76   
e1_submix_3e1          52.85  51.14   708.61  1.029000e+02         0.77   
e1_harmonic_avg        52.99  51.25  1026.15  2.760000e+00         0.66   
e1_min_avg             53.85  52.48  1343.70  2.090000e+00         0.63   
e1_per_al              63.61  61.42      NaN           NaN          NaN   
e1_pal_arithmetic_avg  51.67  45.97   197.92  2.097609e+05         0.79   
e1_pal_geometric_avg   51.80  46.06   387.29  3.283300e+02         0.76   
e1_pal_submix_1e2      61.28  60.66  1437.06  5.950000e+01         0.76   
e1_pal_submix_3e1      52.53  48.58   706.11  1.074600e+02         0.76   
e1_pal_harmonic_avg    52.62  46.70  1004.12  2.780000e+00         0.65   
e1_pal_min_avg         53.60  47.46  1270.66  2.130000e+00         0.62   
e2_ft_all              48.39  41.55    61.81  1.000000e+00         0.83   
e2_baseline              NaN    NaN      NaN           NaN          NaN   
e2_half0               51.68  53.31  2190.40  1.000000e+00         0.47   
e2_half1               51.76  51.16  1803.71  1.000000e+00         0.50   
e2_arithmetic_avg      49.37  43.55    78.93  2.398227e+06         0.82   
e2_geometric_avg       49.64  45.23   202.33  1.442830e+03         0.78   
e2_submix_1e2          59.59  60.03  1296.20  5.831000e+01         0.79   
e2_submix_3e1          50.84  48.54   549.98  1.539800e+02         0.80   
e2_harmonic_avg        50.83  48.37   895.15  3.340000e+00         0.66   
e2_min_avg             51.89  49.79  1161.31  2.660000e+00         0.64   
e2_per_al              63.39  54.18      NaN           NaN          NaN   
e2_pal_arithmetic_avg  49.52  41.31   101.97  1.387229e+06         0.81   
e2_pal_geometric_avg   49.69  41.18   237.08  1.281210e+03         0.77   
e2_pal_submix_1e2      60.54  58.11  1315.26  9.687000e+01         0.78   
e2_pal_submix_3e1      50.69  44.58   570.17  1.944300e+02         0.79   
e2_pal_harmonic_avg    51.01  41.76   912.58  3.390000e+00         0.64   
e2_pal_min_avg         52.22  42.48  1127.29  2.740000e+00         0.62   
e4_ft_all              46.61  37.40    23.94  1.000000e+00         0.86   
e4_baseline              NaN    NaN      NaN           NaN          NaN   
e4_half0               50.18  51.58  2136.16  1.000000e+00         0.49   
e4_half1               49.51  48.59  1903.27  1.000000e+00         0.52   
e4_arithmetic_avg      46.66  38.98    33.27  1.042813e+08         0.85   
e4_geometric_avg       46.96  41.01   103.10  8.738950e+03         0.81   
e4_submix_1e2          59.01  59.03  1045.66  2.043800e+02         0.80   
e4_submix_3e1          48.14  45.21   377.21  8.221800e+02         0.82   
e4_harmonic_avg        48.64  45.34   823.08  4.070000e+00         0.67   
e4_min_avg             49.89  46.97  1059.24  3.350000e+00         0.65   
e4_per_al              66.18  45.37      NaN           NaN          NaN   
e4_pal_arithmetic_avg  47.86  36.40    69.76  5.271034e+07         0.82   
e4_pal_geometric_avg   48.18  36.23   173.73  6.295510e+03         0.79   
e4_pal_submix_1e2      60.38  55.72  1211.44  8.888400e+02         0.79   
e4_pal_submix_3e1      49.03  40.50   504.48  1.291260e+03         0.80   
e4_pal_harmonic_avg    50.45  36.96   984.84  4.120000e+00         0.65   
e4_pal_min_avg         52.14  37.88  1205.45  3.460000e+00         0.64   

                       can_attack_score_30  
ex